<a href="https://colab.research.google.com/github/Motolover/Web_analytics/blob/main/parser_new_V5.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Установка общих либ и запуск основного скрипта парсинга: https://www.joytoy.com/collections/warhammer-action-figure

In [2]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import re
import lxml
import json
import numpy as np
import html
import io
from PIL import Image
from io import BytesIO

In [167]:
import time
import os
import sys

In [168]:
!pip install gspread_formatting

In [169]:
import gspread
import oauth2client
from gspread_dataframe import get_as_dataframe, set_with_dataframe
from gspread_formatting.dataframe import format_with_dataframe
from oauth2client.service_account import ServiceAccountCredentials

In [3]:
!pip install easyocr
import easyocr

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.9/2.9 MB 8.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 908.3/908.3 kB 14.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 307.2/307.2 kB 14.0 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (56.5 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl (124.2 MB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manyli

In [4]:
#from io import BytesIO

In [5]:
input_url = input("Необходимо указать заглавную страницу товарной категории: ")

text = (requests.get(f'{input_url}'))
soup = BeautifulSoup(text.text, 'html')
soup
pagination = soup.find('span', class_= 'total_pages')

if pagination:
    total_pages_text = pagination.text

    # Извлечем число из текст
    total_pages_match = re.search(r'\b(\d+)\b', total_pages_text)
    if total_pages_match:
         total_pages = int(total_pages_match.group(1))
total_pages

Необходимо указать заглавную страницу товарной категории: https://www.joytoy.com/collections/warhammer-action-figure


10

In [6]:
# Заданные переменные
page = 1
max_page = total_pages

# Список для хранения данных всех страниц
all_data = []

# Цикл для перебора страниц
for page in range(page, max_page + 1):
    url = f'{input_url}?page={page}'   #указываем юрл категории
    text = requests.get(url)
    soup = BeautifulSoup(text.text, 'html.parser')

    # Обработка содержимого страницы
    elements = soup.find_all('div', class_='prod_info')

    all_data_page = []
    for e in elements:
        all_data_page.append({
            'name': e.find('a', class_='item_name themes_products_title').text.strip(),
            'price': e.find('div', class_='item_price themes_products_price').text.strip().replace('\n$', '').replace('$', ''),
            'href': e.find('a', class_='item_name themes_products_title')['href']
        })

    img_tags = soup.find_all('img', class_='lazyload transition2')

    data_image = []
    for img_tag in img_tags:
        img_data_srcset = img_tag['data-srcset']
        data_image.append({
            'img': img_data_srcset
        })

    df_page_number = pd.DataFrame(all_data_page)
    df_data_image = pd.DataFrame(data_image)

    df_merged = pd.concat([df_page_number, df_data_image], axis=1)
    all_data.append(df_merged)

# Объединяем данные всех страниц в один DataFrame
final_df = pd.concat(all_data, ignore_index=True)
# Результат
final_df
# Преобразуем DataFrame в строку
#df_str = final_df.to_string(max_colwidth=150)
#print(df_str)

name         price  \
0                        Space Wolves Geigor Fell-Hand   70.84 76.99   
1    Space Wolves Contemptor Dreadnought with Gravi...    82.8 89.99   
2          Ultramarines Librarian in Terminator Armour    73.6 79.99   
3      Ultramarines Terminator Captain Severus Agemman   67.16 72.99   
4                        Ultramarines Terminator Squad  150.3 166.99   
..                                                 ...           ...   
297                         Black Legion Brother Talas            65   
298                    Space Wolves Battle Hunter Pack         99.99   
299                          Invictor Tactical Warsuit        149.99   
300                          Ultramarines Infiltrators     65.79 129   
301                             Ultramarines Incursors     65.79 129   

                                                  href  \
0              /products/space-wolves-geigor-fell-hand   
1    /products/space-wolves-contemptor-dreadnought-...   
2    /products/ultramarines-librarian-in-terminator...   
3    /products/ultramarines-terminator-captain-seve...   
4              /products/ultramarines-terminator-squad   
..                                                 ...   
297               /products/black-legion-brother-talas   
298          /products/space-wolves-battle-hunter-pack   
299                /products/invictor-tactical-warsuit   
300                /products/ultramarines-infiltrators   
301                   /products/ultramarines-incursors   

                                                   img  
0    https://img.joytoy.com/u_file/2404/11/products...  
1    https://img.joytoy.com/u_file/2404/11/products...  
2    https://img.joytoy.com/u_file/2404/04/products...  
3    https://img.joytoy.com/u_file/2404/04/products...  
4    https://img.joytoy.com/u_file/2404/04/products...  
..                                                 ...  
297  https://img.joytoy.com/u_file/2307/11/products...  
298  https://img.joytoy.com/u_file/2307/11/products...  
299  https://img.joytoy.com/u_file/2307/12/products...  
300  https://img.joytoy.com/u_file/2307/11/products...  
301  https://img.joytoy.com/u_file/2307/11/products...  

[302 rows x 4 columns]

## **Создаем столбец Card_link в итоговом датафрейме df_str**

In [7]:
site = 'https://www.joytoy.com'
final_df['card_link'] = site + final_df['href']
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)
final_df

name  \
0                                                        Space Wolves Geigor Fell-Hand   
1                          Space Wolves Contemptor Dreadnought with Gravis Bolt Cannon   
2                                          Ultramarines Librarian in Terminator Armour   
3                                      Ultramarines Terminator Captain Severus Agemman   
4                                                        Ultramarines Terminator Squad   
5                                                                 Blood Angels Veteran   
6                                                 Space Marines Space Wolves Claw Pack   
7                      Sons of Horus Ezekyle Abaddon First Captain of the XVIth Legion   
8                           Sons of Horus Warmaster Horus Primarch of the XVIth Legion   
9                                             Sons of Horus Justaerin Terminator Squad   
10                      Sons of Horus Legion Praetor in Cataphractii Terminator Armour   
11                                                   Sons of Horus MKIV Tactical Squad   
12                         Sons of Horus Contemptor Dreadnought with Gravis Autocannon   
13                                         Sons of Horus Legion Praetor with Power Axe   
14                                                   Sons of Horus MKVI Tactical Squad   
15       Adeptus Custodes Vexilus Praetor in Allarus Terminator Armour Phelam Tolguror   
16                               Adepta Sororitas Penitent Engine with Penitent Flails   
17                                               Imperial Fists Contemptor Dreadnought   
18                                 Imperial Fists Legion Cataphractii Terminator Squad   
19                                                                  Intercessors Group   
20                                        Adeptus Custodes Solar Watch Custodian Guard   
21                                                         Imperial Fists Intercessors   
22                                                           Blood Angels Intercessors   
23                                                           Ultramarines Intercessors   
24                                                           Space Wolves Intercessors   
25                       Imperial Fists Sigismund, First Captain of the lmperial Fists   
26                                           Imperial Fists Mklll Breacher Legionaries   
27                                                          Grey Knights Kaldor Draigo   
28                                                  Dark Angels Deathwing Knight Squad   
29                                                  Dark Angels Deathwing Strikemaster   
30                                                          Imperial Fists Fafnir Rann   
31                                      Imperial Fists Legion Praetor with Power Sword   
32                                          Imperial Fists Mklll Despoiler Legionaries   
33                                           Imperial Fists MkIII Tactical Legionaries   
34                                               Imperial Fists Legion Chaplain Consul   
35                                                           Grey Knights Strike Squad   
36                                                      Grey Knights Interceptor Squad   
37                                                     Adeptus Custodes Blade Champion   
38                       Adeptus Mechanicus Kastelan Robot with Heavy Phosphor Blaster   
39                                            Astra Militarum Cadian Armoured Sentinel   
40                                                       Ultramarines Primaris Captain   
41                                              Black Templars Primaris Sword Brethren   
42                                                    Adepta Sororitas Penitent Engine   
43                                                               Ultramarines Judiciar   
44                              

## **Получения ДАТАФРЕЙМА вместе с SKU**


In [8]:
final_df['SKU'] = ''

for index, row_value in enumerate(final_df['card_link']):
    # Формируем URL, используя значение из card_link
    url = f'{row_value}'

    # Отправляем запрос к URL
    text_card = requests.get(url)

    # Проверяем успешность запроса
    if text_card.status_code == 200:
        # Используем BeautifulSoup для парсинга HTML
        soup = BeautifulSoup(text_card.text, 'html.parser')

        # Находим нужные данные в HTML-коде, например, значение атрибута sku
        div_tags = soup.find_all('div', class_='detail_sku')
        if div_tags:
            first_div_tag = div_tags[0]
            sku_value = first_div_tag.get('sku')

            # Сохраняем результат в final_df
            final_df.at[index, 'SKU'] = sku_value
        else:
            # Если тег с классом 'detail_sku' не найден, можно установить другое значение по умолчанию
            final_df.at[index, 'SKU'] = 'Not Found'
    else:
        # Если запрос не успешен, можно установить другое значение по умолчанию
        final_df.at[index, 'SKU'] = 'Request Failed'

# Выводим результаты
final_df.index.name = '№'
final_df
#print(final_df.to_string(index=False))

name  \
№                                                                                        
0                                                        Space Wolves Geigor Fell-Hand   
1                          Space Wolves Contemptor Dreadnought with Gravis Bolt Cannon   
2                                          Ultramarines Librarian in Terminator Armour   
3                                      Ultramarines Terminator Captain Severus Agemman   
4                                                        Ultramarines Terminator Squad   
5                                                                 Blood Angels Veteran   
6                                                 Space Marines Space Wolves Claw Pack   
7                      Sons of Horus Ezekyle Abaddon First Captain of the XVIth Legion   
8                           Sons of Horus Warmaster Horus Primarch of the XVIth Legion   
9                                             Sons of Horus Justaerin Terminator Squad   
10                      Sons of Horus Legion Praetor in Cataphractii Terminator Armour   
11                                                   Sons of Horus MKIV Tactical Squad   
12                         Sons of Horus Contemptor Dreadnought with Gravis Autocannon   
13                                         Sons of Horus Legion Praetor with Power Axe   
14                                                   Sons of Horus MKVI Tactical Squad   
15       Adeptus Custodes Vexilus Praetor in Allarus Terminator Armour Phelam Tolguror   
16                               Adepta Sororitas Penitent Engine with Penitent Flails   
17                                               Imperial Fists Contemptor Dreadnought   
18                                 Imperial Fists Legion Cataphractii Terminator Squad   
19                                                                  Intercessors Group   
20                                        Adeptus Custodes Solar Watch Custodian Guard   
21                                                         Imperial Fists Intercessors   
22                                                           Blood Angels Intercessors   
23                                                           Ultramarines Intercessors   
24                                                           Space Wolves Intercessors   
25                       Imperial Fists Sigismund, First Captain of the lmperial Fists   
26                                           Imperial Fists Mklll Breacher Legionaries   
27                                                          Grey Knights Kaldor Draigo   
28                                                  Dark Angels Deathwing Knight Squad   
29                                                  Dark Angels Deathwing Strikemaster   
30                                                          Imperial Fists Fafnir Rann   
31                                      Imperial Fists Legion Praetor with Power Sword   
32                                          Imperial Fists Mklll Despoiler Legionaries   
33                                           Imperial Fists MkIII Tactical Legionaries   
34                                               Imperial Fists Legion Chaplain Consul   
35                                                           Grey Knights Strike Squad   
36                                                      Grey Knights Interceptor Squad   
37                                                     Adeptus Custodes Blade Champion   
38                       Adeptus Mechanicus Kastelan Robot with Heavy Phosphor Blaster   
39                                            Astra Militarum Cadian Armoured Sentinel   
40                                                       Ultramarines Primaris Captain   
41                                              Black Templars Primaris Sword Brethren   
42                                                    Adepta Sororitas Penitent Engine   
43                              

In [9]:
images = soup.find_all('div', class_='editor_txt ck-content themes_text_content')[0].find_all('img')

# Получить значения атрибута src для каждого изображения
src_values = [img['src'] for img in images]

# Вывести результат
#print(src_values)

my_string_src_values = ', '.join(src_values)
src_values_format = my_string_src_values.replace(', ', ' | ')
#print(src_values_format)

In [10]:
final_df['all_img_card'] = ''

for index, row_value in enumerate(final_df['card_link']):
    # Формируем URL, используя значение из card_link
    url = f'{row_value}'

    # Отправляем запрос к URL
    text_card = requests.get(url)

    # Проверяем успешность запроса
    if text_card.status_code == 200:
        # Используем BeautifulSoup для парсинга HTML
        soup = BeautifulSoup(text_card.text, 'html.parser')

        # Находим нужные данные в HTML-коде, например, значение атрибута src
        images = soup.find_all('div', class_='editor_txt ck-content themes_text_content')[0].find_all('img')
        if images:
            # для получения значений атрибута src для всех изображений
            img_values = [img.get('src') for img in images]
            my_string_src_values = ', '.join(img_values) # используем метод джоин для для перевода листа img_values в строку
            src_values_format = my_string_src_values.replace(', ', ' | ') # заменяем символ в строке
            # Сохраняем результат в final_df
            final_df.at[index, 'all_img_card'] = src_values_format
        else:
            # Если теги img не найдены, можно установить другое значение по умолчанию
            final_df.at[index, 'all_img_card'] = 'Not Found'
    else:
        # Если запрос не успешен, можно установить другое значение по умолчанию
        final_df.at[index, 'all_img_card'] = 'Request Failed'

# Выводим результаты
final_df.index.name = '№'
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)
final_df

name  \
№                                                                                        
0                                                        Space Wolves Geigor Fell-Hand   
1                          Space Wolves Contemptor Dreadnought with Gravis Bolt Cannon   
2                                          Ultramarines Librarian in Terminator Armour   
3                                      Ultramarines Terminator Captain Severus Agemman   
4                                                        Ultramarines Terminator Squad   
5                                                                 Blood Angels Veteran   
6                                                 Space Marines Space Wolves Claw Pack   
7                      Sons of Horus Ezekyle Abaddon First Captain of the XVIth Legion   
8                           Sons of Horus Warmaster Horus Primarch of the XVIth Legion   
9                                             Sons of Horus Justaerin Terminator Squad   
10                      Sons of Horus Legion Praetor in Cataphractii Terminator Armour   
11                                                   Sons of Horus MKIV Tactical Squad   
12                         Sons of Horus Contemptor Dreadnought with Gravis Autocannon   
13                                         Sons of Horus Legion Praetor with Power Axe   
14                                                   Sons of Horus MKVI Tactical Squad   
15       Adeptus Custodes Vexilus Praetor in Allarus Terminator Armour Phelam Tolguror   
16                               Adepta Sororitas Penitent Engine with Penitent Flails   
17                                               Imperial Fists Contemptor Dreadnought   
18                                 Imperial Fists Legion Cataphractii Terminator Squad   
19                                                                  Intercessors Group   
20                                        Adeptus Custodes Solar Watch Custodian Guard   
21                                                         Imperial Fists Intercessors   
22                                                           Blood Angels Intercessors   
23                                                           Ultramarines Intercessors   
24                                                           Space Wolves Intercessors   
25                       Imperial Fists Sigismund, First Captain of the lmperial Fists   
26                                           Imperial Fists Mklll Breacher Legionaries   
27                                                          Grey Knights Kaldor Draigo   
28                                                  Dark Angels Deathwing Knight Squad   
29                                                  Dark Angels Deathwing Strikemaster   
30                                                          Imperial Fists Fafnir Rann   
31                                      Imperial Fists Legion Praetor with Power Sword   
32                                          Imperial Fists Mklll Despoiler Legionaries   
33                                           Imperial Fists MkIII Tactical Legionaries   
34                                               Imperial Fists Legion Chaplain Consul   
35                                                           Grey Knights Strike Squad   
36                                                      Grey Knights Interceptor Squad   
37                                                     Adeptus Custodes Blade Champion   
38                       Adeptus Mechanicus Kastelan Robot with Heavy Phosphor Blaster   
39                                            Astra Militarum Cadian Armoured Sentinel   
40                                                       Ultramarines Primaris Captain   
41                                              Black Templars Primaris Sword Brethren   
42                                                    Adepta Sororitas Penitent Engine   
43                              

### **ПАРСИНГ КАРТОЧЕК С РЯДОМ ПОЗИЦИЙ ВНТУРИ КАРТОЧКИ**

In [11]:
filtered_df = final_df[final_df['SKU'].str.contains('ZH', case=False)]
filtered_df

name          price  \
№                                                                        
4                         Ultramarines Terminator Squad   150.3 166.99   
5                                  Blood Angels Veteran     117 129.99   
6                  Space Marines Space Wolves Claw Pack     117 129.99   
9              Sons of Horus Justaerin Terminator Squad         229.99   
11                    Sons of Horus MKIV Tactical Squad         181.96   
14                    Sons of Horus MKVI Tactical Squad         171.96   
18  Imperial Fists Legion Cataphractii Terminator Squad         231.96   
19                                   Intercessors Group          99.96   
20         Adeptus Custodes Solar Watch Custodian Guard         137.97   
26            Imperial Fists Mklll Breacher Legionaries  129.99 139.99   
28                   Dark Angels Deathwing Knight Squad  175.99 191.99   
29                   Dark Angels Deathwing Strikemaster  179.99 195.99   
32           Imperial Fists Mklll Despoiler Legionaries    79.99 87.99   
33            Imperial Fists MkIII Tactical Legionaries  166.99 181.99   
35                            Grey Knights Strike Squad     119 139.99   
36                       Grey Knights Interceptor Squad     119 139.99   
41               Black Templars Primaris Sword Brethren         128.97   
48                       Ultramarines Desolation Marine         139.99   
51            Primaris Space Marines Bladeguard Veteran         171.96   

                                                               href  \
№                                                                     
4                           /products/ultramarines-terminator-squad   
5                                    /products/blood-angels-veteran   
6                    /products/space-marines-space-wolves-claw-pack   
9                /products/sons-of-horus-justaerin-terminator-squad   
11                      /products/sons-of-horus-mkiv-tactical-squad   
14                      /products/sons-of-horus-mkvi-tactical-squad   
18    /products/imperial-fists-legion-cataphractii-terminator-squad   
19                                           /products/intercessors   
20           /products/adeptus-custodes-solar-watch-custodian-guard   
26              /products/imperial-fists-mklll-breacher-legionaries   
28                     /products/dark-angels-deathwing-knight-squad   
29                    /products/dark-angels-deathwing-action-figure   
32             /products/imperial-fists-mklll-despoiler-legionaries   
33               /products/imperial-fists-mklli-tacticallegionaries   
35                              /products/grey-knights-strike-squad   
36                         /products/grey-knights-interceptor-squad   
41                 /products/black-templars-primaris-sword-brethren   
48  /products/ultramarines-desolation-sergeant-with-vengor-launcher   
51              /products/primaris-space-marines-bladeguard-veteran   

                                                                                                                         img  \
№                                                                                                                              
4   https://img.joytoy.com/u_file/2404/04/products/c86d06dd31.jpg?x-oss-process=image/quality,q_80/resize,m_lfit,h_600,w_500   
5   https://img.joytoy.com/u_file/2404/03/products/6a0ebc7628.jpg?x-oss-process=image/quality,q_80/resize,m_lfit,h_600,w_500   
6   https://img.joytoy.com/u_file/2403/25/products/ba4c491422.jpg?x-oss-process=image/quality,q_80/resize,m_lfit,h_600,w_500   
9   https://img.joytoy.com/u_file/2403/05/products/ece4668001.jpg?x-oss-process=image/quality,q_80/resize,m_lfit,h_600,w_500   
11  https://img.joytoy.com/u_file/2402/29/products/19be8268da.jpg?x-oss-process=image/quality,q_80/resize,m_lfit,h_600,w_500   
14  https://img.joytoy.com/u_file/2402/15/products/b9d8c69a59.jpg?x-oss-process=image/quality,q_80/resize,m_

In [12]:
data_list = []

def decode_html_entities(string):
    return html.unescape(string)

#url2 = 'https://www.joytoy.com/products/blood-angels-veteran?VariantsId=10114'
for index, row_value in enumerate(filtered_df['card_link']):
    # Формируем URL, используя значение из card_link
    url = f'{row_value}'
    response = requests.get(url)

    if response.status_code == 200:
      soup = BeautifulSoup(response.text, 'html.parser')

    # Находим все элементы input с id='ext_attr'
    attr_box_elements = soup.find_all('input', id='ext_attr')

    # Проверяем, найдены ли элементы
    if attr_box_elements:
        # Проходимся по всем найденным элементам
        for attr_box_element in attr_box_elements:
            # Получаем значение атрибута value
            value = attr_box_element.get('value')

            # Декодируем HTML-сущности в строке
            decoded_value = decode_html_entities(value)

            try:
                # Преобразуем строку в объект Python (словарь)
                data = json.loads(decoded_value)
                if isinstance(data, dict):
                  data_list.append(data)
                # Выводим полученные данные
                #print(data)
            except json.JSONDecodeError as e:
                print("Ошибка при разборе JSON:", e)
    else:
        print("Элементы с id='ext_attr' не найдены.")

#result_df = pd.DataFrame(data_list)

In [13]:
data_list

[{'Total': {'set of 3': [['166.99',
     '194',
     '1.05',
     'ZH233047',
     '0.00',
     '4142',
     '10126',
     '0',
     '1']],
   'Sergeant with Power Sword and Teleport Homer': [['57.99',
     '196',
     '0.35',
     '6973130379923',
     '0.00',
     '4144',
     '10127',
     '0',
     '0']],
   'Terminator with Storm Bolter': [['54.99',
     '194',
     '0.35',
     '6973130379930',
     '0.00',
     '4150',
     '10128',
     '0',
     '0']],
   'Terminator with Assault Cannon': [['54.99',
     '195',
     '0.35',
     '6973130379947',
     '0.00',
     '4156',
     '10129',
     '0',
     '0']]}},
 {'Total': {'SET OF 4': [['129.99',
     '97',
     '1.4',
     'ZH72899602',
     '0.00',
     '4084',
     '10114',
     '0',
     '1']],
   'Laenatus': [['32.99',
     '100',
     '0.35',
     '6973130373402',
     '0.00',
     '4086',
     '10115',
     '0',
     '0']],
   'Vigna': [['32.99',
     '99',
     '0.35',
     '6973130373396',
     '0.00',
     '4091',
     

In [14]:
processed_data = []

# Проходим по каждому элементу списка
for entry in data_list:
    # Получаем словарь 'Total' из текущего элемента
    total_data = entry.get('Total', {})
    # Проходим по каждому ключу (названию продукта) в словаре "Total"
    for product_name, value in total_data.items():
        # Проходим по каждому списку с данными о продукте
        for item in value:
            # Создаем словарь с данными о продукте
            product_info = {
                'Product Name': product_name,
                'Price': item[0],
                'SKU': item[3],
                'VariantsId': item[6]
            }
            processed_data.append(product_info)

# Преобразуем список словарей в DataFrame Pandas
cards_position_df = pd.DataFrame(processed_data)
cards_position_df

Product Name   Price  \
0                                                    set of 3  166.99   
1                Sergeant with Power Sword and Teleport Homer   57.99   
2                                Terminator with Storm Bolter   54.99   
3                              Terminator with Assault Cannon   54.99   
4                                                    SET OF 4  129.99   
5                                                    Laenatus   32.99   
6                                                       Vigna   32.99   
7                                                       Salus   32.99   
8                                                    Alberigo   32.99   
9                                                    Set of 4  129.99   
10                                    Leader -Logan Ghostwolf   32.99   
11                                             Brother Gunnar   32.99   
12                                               Brother Olaf   32.99   
13                                           Brother Torrvald   32.99   
14                                                   Set of 4  229.99   
15                          Justaerin with Carsoran Power Axe   57.99   
16                             Justaerin with Lightning Claws   57.99   
17                              Justaerin with Thunder Hammer   57.99   
18                  Justaerin with Multi-melta and Power Maul   57.99   
19                                                   Set of 4  181.96   
20                                   Sergeant with Power Fist   46.99   
21                              Legionary with Legion Vexilla   46.99   
22                                      Legionary with Flamer   43.99   
23                                      Legionary with Bolter   43.99   
24                                                   Set of 4  171.96   
25                                  Sergeant with Power Sword   43.99   
26                              Legionary with Legion Vexilla   43.99   
27                                  Legionary with Nuncio Vox   41.99   
28                         Legionary with Bolter & Chainblade   41.99   
29                                                   Set of 4  231.96   
30              Legion Cataphractii Sergeant with Power Sword   57.99   
31             Legion Cataphractii Sergeant with Heavy Flamer   57.99   
32                Legion Cataphractii Sergeant with Chainfist   57.99   
33          Legion Cataphractii Sergeant with Lightning Claws   57.99   
34                                                   Set of 3  137.97   
35  Custodian Guard with Sentinel Blade and Praesidium Shield   44.99   
36                        Custodian Guard with Guardian Spear   44.99   
37                                            Vexilus Praetor   44.99   
38                                                   Set of 3  129.99   
39                               Sergeant with Thunder Hammer   46.99   
40                          Legion Breacher with Graviton Gun   46.99   
41                             Legion Breacher with Lascutter   46.99   
42                                                   Set of 3  175.99   
43                                    Deathwing Knight Master   63.99   
44                                         Deathwing Knight 1   63.99   
45                                         Deathwing Knight 2   63.99   
46                                                   Set of 3  179.99   
47                    Deathwing Strikemaster with Power Sword   67.99   
48                      Deathwing Ancient with Company Banner   63.99   
49                                         Deathwing Champion   63.99   
50                                                   Set of 2   79.99   
51                                Sergeant with Plasma Pistol   43.99   
52                           Legion Despoiler with Chainsword   43.99   
53                                                   Set of 4  166.99   
54                                

In [15]:
#file_path = r"C:\Users\Fibo\Проекты\WH40\cards_position_df.xlsx"

#cards_position_df.to_excel(file_path, index=False)

In [16]:
# Подлкючаем информацию из final_df (ссылки) к датафрейу с карточками

#cards_position_df2 = pd.merge(cards_position_df, final_df, left_index=True, right_index=True, how='left')
cards_position_df2 = cards_position_df.merge(final_df, on=["SKU"])
cards_position_df2 = cards_position_df2[['Product Name','SKU', 'VariantsId', 'card_link']]
cards_position_df2  = cards_position_df2[cards_position_df2 ['SKU'].str.contains('ZH', case=False)]
cards_position_df2

Product Name          SKU VariantsId  \
0                         set of 3     ZH233047      10126   
1                         SET OF 4   ZH72899602      10114   
6                         Set of 4   ZH02192633      10095   
7                         Set of 4   ZH18253249      10090   
8                         Set of 4   ZH02968972      10085   
9                         Set of 4   ZH66738097      10065   
10                        Set of 4   ZH74819804      10060   
11                        Set of 3     ZH364350      10056   
12                        Set of 3  ZH107114121      10052   
13                        Set of 3     ZH900613      10048   
14                        Set of 3     ZH697683      10044   
15                        Set of 2   ZH90849091      10041   
16                        Set of 4   ZH46536077      10036   
17                        Set of 3     ZH950815      10032   
18                        Set of 3     ZH647188      10028   
19                        Set of 3     ZH462239      10024   
20                        Set of 3     ZH031027      10020   
21  Bladeguard Veteran 4-piece set   ZH71889501      10013   

                                                                                card_link  
0                           https://www.joytoy.com/products/ultramarines-terminator-squad  
1                                    https://www.joytoy.com/products/blood-angels-veteran  
6                    https://www.joytoy.com/products/space-marines-space-wolves-claw-pack  
7                https://www.joytoy.com/products/sons-of-horus-justaerin-terminator-squad  
8                       https://www.joytoy.com/products/sons-of-horus-mkiv-tactical-squad  
9                       https://www.joytoy.com/products/sons-of-horus-mkvi-tactical-squad  
10    https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminator-squad  
11           https://www.joytoy.com/products/adeptus-custodes-solar-watch-custodian-guard  
12              https://www.joytoy.com/products/imperial-fists-mklll-breacher-legionaries  
13                     https://www.joytoy.com/products/dark-angels-deathwing-knight-squad  
14                    https://www.joytoy.com/products/dark-angels-deathwing-action-figure  
15             https://www.joytoy.com/products/imperial-fists-mklll-despoiler-legionaries  
16               https://www.joytoy.com/products/imperial-fists-mklli-tacticallegionaries  
17                              https://www.joytoy.com/products/grey-knights-strike-squad  
18                         https://www.joytoy.com/products/grey-knights-interceptor-squad  
19                 https://www.joytoy.com/products/black-templars-primaris-sword-brethren  
20  https://www.joytoy.com/products/ultramarines-desolation-sergeant-with-vengor-launcher  
21              https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran

In [17]:
#Извлекаем и создаем столбец с количество карточек в наборе
cards_position_df2["num_step"] = pd.to_numeric(cards_position_df2["Product Name"].str.extract(r"\b(\d+)\b")[0], errors="coerce")
cards_position_df2

Product Name          SKU VariantsId  \
0                         set of 3     ZH233047      10126   
1                         SET OF 4   ZH72899602      10114   
6                         Set of 4   ZH02192633      10095   
7                         Set of 4   ZH18253249      10090   
8                         Set of 4   ZH02968972      10085   
9                         Set of 4   ZH66738097      10065   
10                        Set of 4   ZH74819804      10060   
11                        Set of 3     ZH364350      10056   
12                        Set of 3  ZH107114121      10052   
13                        Set of 3     ZH900613      10048   
14                        Set of 3     ZH697683      10044   
15                        Set of 2   ZH90849091      10041   
16                        Set of 4   ZH46536077      10036   
17                        Set of 3     ZH950815      10032   
18                        Set of 3     ZH647188      10028   
19                        Set of 3     ZH462239      10024   
20                        Set of 3     ZH031027      10020   
21  Bladeguard Veteran 4-piece set   ZH71889501      10013   

                                                                                card_link  \
0                           https://www.joytoy.com/products/ultramarines-terminator-squad   
1                                    https://www.joytoy.com/products/blood-angels-veteran   
6                    https://www.joytoy.com/products/space-marines-space-wolves-claw-pack   
7                https://www.joytoy.com/products/sons-of-horus-justaerin-terminator-squad   
8                       https://www.joytoy.com/products/sons-of-horus-mkiv-tactical-squad   
9                       https://www.joytoy.com/products/sons-of-horus-mkvi-tactical-squad   
10    https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminator-squad   
11           https://www.joytoy.com/products/adeptus-custodes-solar-watch-custodian-guard   
12              https://www.joytoy.com/products/imperial-fists-mklll-breacher-legionaries   
13                     https://www.joytoy.com/products/dark-angels-deathwing-knight-squad   
14                    https://www.joytoy.com/products/dark-angels-deathwing-action-figure   
15             https://www.joytoy.com/products/imperial-fists-mklll-despoiler-legionaries   
16               https://www.joytoy.com/products/imperial-fists-mklli-tacticallegionaries   
17                              https://www.joytoy.com/products/grey-knights-strike-squad   
18                         https://www.joytoy.com/products/grey-knights-interceptor-squad   
19                 https://www.joytoy.com/products/black-templars-primaris-sword-brethren   
20  https://www.joytoy.com/products/ultramarines-desolation-sergeant-with-vengor-launcher   
21              https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran   

    num_step  
0          3  
1          4  
6          4  
7          4  
8          4  
9          4  
10         4  
11         3  
12         3  
13         3  
14         3  
15         2  
16         4  
17         3  
18         3  
19         3  
20         3  
21         4

In [18]:
#list(range(row['col1'], row['col2']))

In [19]:
cards_position_df2['VariantsId'] = cards_position_df2['VariantsId'].astype(int)
cards_position_df2['num_step'] = cards_position_df2['num_step'].astype(int)

# Ваша функция, которую вы хотите применить к каждой строке
def my_function(row):
    # например, вы хотите сложить значения столбцов A и B
    return row['VariantsId'] + row['num_step']

# Создаем пустой столбец 'result'
cards_position_df2['max_variantid'] = None

# Применяем функцию к каждой строке DataFrame с помощью цикла for
for index, row in cards_position_df2.iterrows():
    cards_position_df2.at[index, 'max_variantid'] = my_function(row)

cards_position_df2

Product Name          SKU  VariantsId  \
0                         set of 3     ZH233047       10126   
1                         SET OF 4   ZH72899602       10114   
6                         Set of 4   ZH02192633       10095   
7                         Set of 4   ZH18253249       10090   
8                         Set of 4   ZH02968972       10085   
9                         Set of 4   ZH66738097       10065   
10                        Set of 4   ZH74819804       10060   
11                        Set of 3     ZH364350       10056   
12                        Set of 3  ZH107114121       10052   
13                        Set of 3     ZH900613       10048   
14                        Set of 3     ZH697683       10044   
15                        Set of 2   ZH90849091       10041   
16                        Set of 4   ZH46536077       10036   
17                        Set of 3     ZH950815       10032   
18                        Set of 3     ZH647188       10028   
19                        Set of 3     ZH462239       10024   
20                        Set of 3     ZH031027       10020   
21  Bladeguard Veteran 4-piece set   ZH71889501       10013   

                                                                                card_link  \
0                           https://www.joytoy.com/products/ultramarines-terminator-squad   
1                                    https://www.joytoy.com/products/blood-angels-veteran   
6                    https://www.joytoy.com/products/space-marines-space-wolves-claw-pack   
7                https://www.joytoy.com/products/sons-of-horus-justaerin-terminator-squad   
8                       https://www.joytoy.com/products/sons-of-horus-mkiv-tactical-squad   
9                       https://www.joytoy.com/products/sons-of-horus-mkvi-tactical-squad   
10    https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminator-squad   
11           https://www.joytoy.com/products/adeptus-custodes-solar-watch-custodian-guard   
12              https://www.joytoy.com/products/imperial-fists-mklll-breacher-legionaries   
13                     https://www.joytoy.com/products/dark-angels-deathwing-knight-squad   
14                    https://www.joytoy.com/products/dark-angels-deathwing-action-figure   
15             https://www.joytoy.com/products/imperial-fists-mklll-despoiler-legionaries   
16               https://www.joytoy.com/products/imperial-fists-mklli-tacticallegionaries   
17                              https://www.joytoy.com/products/grey-knights-strike-squad   
18                         https://www.joytoy.com/products/grey-knights-interceptor-squad   
19                 https://www.joytoy.com/products/black-templars-primaris-sword-brethren   
20  https://www.joytoy.com/products/ultramarines-desolation-sergeant-with-vengor-launcher   
21              https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran   

    num_step max_variantid  
0          3         10129  
1          4         10118  
6          4         10099  
7          4         10094  
8          4         10089  
9          4         10069  
10         4         10064  
11         3         10059  
12         3         10055  
13         3         10051  
14         3         10047  
15         2         10043  
16         4         10040  
17         3         10035  
18         3         10031  
19         3         10027  
20         3         10023  
21         4         10017

In [20]:
# Ваша функция, которую вы хотите применить к каждой строке
def my_function(row):
    # например, вы хотите сложить значения столбцов A и B
    return list(range(row['VariantsId'], row['max_variantid']))

cards_position_df2['range_id'] = None

# Применяем функцию к каждой строке DataFrame с помощью цикла for
for index, row in cards_position_df2.iterrows():
    cards_position_df2.at[index, 'range_id'] = my_function(row)

cards_position_df2

Product Name          SKU  VariantsId  \
0                         set of 3     ZH233047       10126   
1                         SET OF 4   ZH72899602       10114   
6                         Set of 4   ZH02192633       10095   
7                         Set of 4   ZH18253249       10090   
8                         Set of 4   ZH02968972       10085   
9                         Set of 4   ZH66738097       10065   
10                        Set of 4   ZH74819804       10060   
11                        Set of 3     ZH364350       10056   
12                        Set of 3  ZH107114121       10052   
13                        Set of 3     ZH900613       10048   
14                        Set of 3     ZH697683       10044   
15                        Set of 2   ZH90849091       10041   
16                        Set of 4   ZH46536077       10036   
17                        Set of 3     ZH950815       10032   
18                        Set of 3     ZH647188       10028   
19                        Set of 3     ZH462239       10024   
20                        Set of 3     ZH031027       10020   
21  Bladeguard Veteran 4-piece set   ZH71889501       10013   

                                                                                card_link  \
0                           https://www.joytoy.com/products/ultramarines-terminator-squad   
1                                    https://www.joytoy.com/products/blood-angels-veteran   
6                    https://www.joytoy.com/products/space-marines-space-wolves-claw-pack   
7                https://www.joytoy.com/products/sons-of-horus-justaerin-terminator-squad   
8                       https://www.joytoy.com/products/sons-of-horus-mkiv-tactical-squad   
9                       https://www.joytoy.com/products/sons-of-horus-mkvi-tactical-squad   
10    https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminator-squad   
11           https://www.joytoy.com/products/adeptus-custodes-solar-watch-custodian-guard   
12              https://www.joytoy.com/products/imperial-fists-mklll-breacher-legionaries   
13                     https://www.joytoy.com/products/dark-angels-deathwing-knight-squad   
14                    https://www.joytoy.com/products/dark-angels-deathwing-action-figure   
15             https://www.joytoy.com/products/imperial-fists-mklll-despoiler-legionaries   
16               https://www.joytoy.com/products/imperial-fists-mklli-tacticallegionaries   
17                              https://www.joytoy.com/products/grey-knights-strike-squad   
18                         https://www.joytoy.com/products/grey-knights-interceptor-squad   
19                 https://www.joytoy.com/products/black-templars-primaris-sword-brethren   
20  https://www.joytoy.com/products/ultramarines-desolation-sergeant-with-vengor-launcher   
21              https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran   

    num_step max_variantid                      range_id  
0          3         10129         [10126, 10127, 10128]  
1          4         10118  [10114, 10115, 10116, 10117]  
6          4         10099  [10095, 10096, 10097, 10098]  
7          4         10094  [10090, 10091, 10092, 10093]  
8          4         10089  [10085, 10086, 10087, 10088]  
9          4         10069  [10065, 10066, 10067, 10068]  
10         4         10064  [10060, 10061, 10062, 10063]  
11         3         10059         [10056, 10057, 10058]  
12         3         10055         [10052, 10053, 10054]  
13         3         10051         [10048, 10049, 10050]  
14         3         10047         [10044, 10045, 10046]  
15         2         10043                [10041, 10042]  
16         4         10040  [10036, 10037, 10038, 10039]  
17         3         10035         [10032, 10033, 10034]  
18         3         10031         [10028, 10029, 10030]  
19         3         10027         [10024, 10025, 10026]  
20         3         10023         [10020, 10021, 100

In [21]:
#cards_position_df2 = cards_position_df2.explode('range_id')
cards_position_df2[['var1', 'var2', 'var3', 'var4']] = cards_position_df2['range_id'].apply(pd.Series)

In [22]:
#Создаем ссылки для каждого варианта
cards_position_var1 = cards_position_df2[["card_link", "var1"]]
cards_position_var1 = cards_position_var1.drop_duplicates(subset=['card_link', 'var1'])
cards_position_var1 = cards_position_var1.rename(columns={'var1': 'variant_id'})
cards_position_var1['variant_id'] = cards_position_var1['variant_id'].astype(int) # Убираем нули значений
cards_position_var1
#cards_position_var1.drop_duplicates()

card_link  \
0                           https://www.joytoy.com/products/ultramarines-terminator-squad   
1                                    https://www.joytoy.com/products/blood-angels-veteran   
6                    https://www.joytoy.com/products/space-marines-space-wolves-claw-pack   
7                https://www.joytoy.com/products/sons-of-horus-justaerin-terminator-squad   
8                       https://www.joytoy.com/products/sons-of-horus-mkiv-tactical-squad   
9                       https://www.joytoy.com/products/sons-of-horus-mkvi-tactical-squad   
10    https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminator-squad   
11           https://www.joytoy.com/products/adeptus-custodes-solar-watch-custodian-guard   
12              https://www.joytoy.com/products/imperial-fists-mklll-breacher-legionaries   
13                     https://www.joytoy.com/products/dark-angels-deathwing-knight-squad   
14                    https://www.joytoy.com/products/dark-angels-deathwing-action-figure   
15             https://www.joytoy.com/products/imperial-fists-mklll-despoiler-legionaries   
16               https://www.joytoy.com/products/imperial-fists-mklli-tacticallegionaries   
17                              https://www.joytoy.com/products/grey-knights-strike-squad   
18                         https://www.joytoy.com/products/grey-knights-interceptor-squad   
19                 https://www.joytoy.com/products/black-templars-primaris-sword-brethren   
20  https://www.joytoy.com/products/ultramarines-desolation-sergeant-with-vengor-launcher   
21              https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran   

    variant_id  
0        10126  
1        10114  
6        10095  
7        10090  
8        10085  
9        10065  
10       10060  
11       10056  
12       10052  
13       10048  
14       10044  
15       10041  
16       10036  
17       10032  
18       10028  
19       10024  
20       10020  
21       10013

In [23]:
cards_position_var2 = cards_position_df2[["card_link", "var2"]]
cards_position_var2 = cards_position_var2.drop_duplicates(subset=['card_link', 'var2'])
cards_position_var2 = cards_position_var2.rename(columns={'var2': 'variant_id'})
cards_position_var2['variant_id'] = cards_position_var2['variant_id'].astype(int) # Убираем нули значений
cards_position_var2

card_link  \
0                           https://www.joytoy.com/products/ultramarines-terminator-squad   
1                                    https://www.joytoy.com/products/blood-angels-veteran   
6                    https://www.joytoy.com/products/space-marines-space-wolves-claw-pack   
7                https://www.joytoy.com/products/sons-of-horus-justaerin-terminator-squad   
8                       https://www.joytoy.com/products/sons-of-horus-mkiv-tactical-squad   
9                       https://www.joytoy.com/products/sons-of-horus-mkvi-tactical-squad   
10    https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminator-squad   
11           https://www.joytoy.com/products/adeptus-custodes-solar-watch-custodian-guard   
12              https://www.joytoy.com/products/imperial-fists-mklll-breacher-legionaries   
13                     https://www.joytoy.com/products/dark-angels-deathwing-knight-squad   
14                    https://www.joytoy.com/products/dark-angels-deathwing-action-figure   
15             https://www.joytoy.com/products/imperial-fists-mklll-despoiler-legionaries   
16               https://www.joytoy.com/products/imperial-fists-mklli-tacticallegionaries   
17                              https://www.joytoy.com/products/grey-knights-strike-squad   
18                         https://www.joytoy.com/products/grey-knights-interceptor-squad   
19                 https://www.joytoy.com/products/black-templars-primaris-sword-brethren   
20  https://www.joytoy.com/products/ultramarines-desolation-sergeant-with-vengor-launcher   
21              https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran   

    variant_id  
0        10127  
1        10115  
6        10096  
7        10091  
8        10086  
9        10066  
10       10061  
11       10057  
12       10053  
13       10049  
14       10045  
15       10042  
16       10037  
17       10033  
18       10029  
19       10025  
20       10021  
21       10014

In [24]:
cards_position_var3 = cards_position_df2[["card_link", "var3"]]
cards_position_var3 = cards_position_var3.drop_duplicates(subset=['card_link', 'var3'])
cards_position_var3 = cards_position_var3.rename(columns={'var3': 'variant_id'})

cards_position_var3 = cards_position_var3.dropna()
cards_position_var3['variant_id'] = cards_position_var3['variant_id'].astype(int) # Убираем нули значений
cards_position_var3

card_link  \
0                           https://www.joytoy.com/products/ultramarines-terminator-squad   
1                                    https://www.joytoy.com/products/blood-angels-veteran   
6                    https://www.joytoy.com/products/space-marines-space-wolves-claw-pack   
7                https://www.joytoy.com/products/sons-of-horus-justaerin-terminator-squad   
8                       https://www.joytoy.com/products/sons-of-horus-mkiv-tactical-squad   
9                       https://www.joytoy.com/products/sons-of-horus-mkvi-tactical-squad   
10    https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminator-squad   
11           https://www.joytoy.com/products/adeptus-custodes-solar-watch-custodian-guard   
12              https://www.joytoy.com/products/imperial-fists-mklll-breacher-legionaries   
13                     https://www.joytoy.com/products/dark-angels-deathwing-knight-squad   
14                    https://www.joytoy.com/products/dark-angels-deathwing-action-figure   
16               https://www.joytoy.com/products/imperial-fists-mklli-tacticallegionaries   
17                              https://www.joytoy.com/products/grey-knights-strike-squad   
18                         https://www.joytoy.com/products/grey-knights-interceptor-squad   
19                 https://www.joytoy.com/products/black-templars-primaris-sword-brethren   
20  https://www.joytoy.com/products/ultramarines-desolation-sergeant-with-vengor-launcher   
21              https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran   

    variant_id  
0        10128  
1        10116  
6        10097  
7        10092  
8        10087  
9        10067  
10       10062  
11       10058  
12       10054  
13       10050  
14       10046  
16       10038  
17       10034  
18       10030  
19       10026  
20       10022  
21       10015

In [25]:
cards_position_var4 = cards_position_df2[["card_link", "var4"]]
cards_position_var4 = cards_position_var4.drop_duplicates(subset=['card_link', 'var4'])
cards_position_var4 = cards_position_var4.rename(columns={'var4': 'variant_id'})

cards_position_var4 = cards_position_var4.dropna()
cards_position_var4['variant_id'] = cards_position_var4['variant_id'].astype(int) # Убираем нули значений
cards_position_var4

card_link  \
1                                  https://www.joytoy.com/products/blood-angels-veteran   
6                  https://www.joytoy.com/products/space-marines-space-wolves-claw-pack   
7              https://www.joytoy.com/products/sons-of-horus-justaerin-terminator-squad   
8                     https://www.joytoy.com/products/sons-of-horus-mkiv-tactical-squad   
9                     https://www.joytoy.com/products/sons-of-horus-mkvi-tactical-squad   
10  https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminator-squad   
16             https://www.joytoy.com/products/imperial-fists-mklli-tacticallegionaries   
21            https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran   

    variant_id  
1        10117  
6        10098  
7        10093  
8        10088  
9        10068  
10       10063  
16       10039  
21       10016

In [26]:
#Последний номер подкарточки из столцба max_variantid
cards_position_max_variantid = cards_position_df2[["card_link", "max_variantid"]]
cards_position_max_variantid = cards_position_max_variantid.drop_duplicates(subset=['card_link', 'max_variantid'])
cards_position_max_variantid = cards_position_max_variantid.rename(columns={'max_variantid': 'variant_id'})
cards_position_max_variantid

card_link  \
0                           https://www.joytoy.com/products/ultramarines-terminator-squad   
1                                    https://www.joytoy.com/products/blood-angels-veteran   
6                    https://www.joytoy.com/products/space-marines-space-wolves-claw-pack   
7                https://www.joytoy.com/products/sons-of-horus-justaerin-terminator-squad   
8                       https://www.joytoy.com/products/sons-of-horus-mkiv-tactical-squad   
9                       https://www.joytoy.com/products/sons-of-horus-mkvi-tactical-squad   
10    https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminator-squad   
11           https://www.joytoy.com/products/adeptus-custodes-solar-watch-custodian-guard   
12              https://www.joytoy.com/products/imperial-fists-mklll-breacher-legionaries   
13                     https://www.joytoy.com/products/dark-angels-deathwing-knight-squad   
14                    https://www.joytoy.com/products/dark-angels-deathwing-action-figure   
15             https://www.joytoy.com/products/imperial-fists-mklll-despoiler-legionaries   
16               https://www.joytoy.com/products/imperial-fists-mklli-tacticallegionaries   
17                              https://www.joytoy.com/products/grey-knights-strike-squad   
18                         https://www.joytoy.com/products/grey-knights-interceptor-squad   
19                 https://www.joytoy.com/products/black-templars-primaris-sword-brethren   
20  https://www.joytoy.com/products/ultramarines-desolation-sergeant-with-vengor-launcher   
21              https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran   

   variant_id  
0       10129  
1       10118  
6       10099  
7       10094  
8       10089  
9       10069  
10      10064  
11      10059  
12      10055  
13      10051  
14      10047  
15      10043  
16      10040  
17      10035  
18      10031  
19      10027  
20      10023  
21      10017

In [27]:
#Формируем датафрейм на основе предыдущих датасетов
union_cardspositions = pd.concat([cards_position_var1, cards_position_var2, cards_position_var3, cards_position_var4, cards_position_max_variantid])
union_cardspositions = union_cardspositions.dropna(subset=['variant_id']).astype(str)
union_cardspositions

card_link  \
0                           https://www.joytoy.com/products/ultramarines-terminator-squad   
1                                    https://www.joytoy.com/products/blood-angels-veteran   
6                    https://www.joytoy.com/products/space-marines-space-wolves-claw-pack   
7                https://www.joytoy.com/products/sons-of-horus-justaerin-terminator-squad   
8                       https://www.joytoy.com/products/sons-of-horus-mkiv-tactical-squad   
9                       https://www.joytoy.com/products/sons-of-horus-mkvi-tactical-squad   
10    https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminator-squad   
11           https://www.joytoy.com/products/adeptus-custodes-solar-watch-custodian-guard   
12              https://www.joytoy.com/products/imperial-fists-mklll-breacher-legionaries   
13                     https://www.joytoy.com/products/dark-angels-deathwing-knight-squad   
14                    https://www.joytoy.com/products/dark-angels-deathwing-action-figure   
15             https://www.joytoy.com/products/imperial-fists-mklll-despoiler-legionaries   
16               https://www.joytoy.com/products/imperial-fists-mklli-tacticallegionaries   
17                              https://www.joytoy.com/products/grey-knights-strike-squad   
18                         https://www.joytoy.com/products/grey-knights-interceptor-squad   
19                 https://www.joytoy.com/products/black-templars-primaris-sword-brethren   
20  https://www.joytoy.com/products/ultramarines-desolation-sergeant-with-vengor-launcher   
21              https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran   
0                           https://www.joytoy.com/products/ultramarines-terminator-squad   
1                                    https://www.joytoy.com/products/blood-angels-veteran   
6                    https://www.joytoy.com/products/space-marines-space-wolves-claw-pack   
7                https://www.joytoy.com/products/sons-of-horus-justaerin-terminator-squad   
8                       https://www.joytoy.com/products/sons-of-horus-mkiv-tactical-squad   
9                       https://www.joytoy.com/products/sons-of-horus-mkvi-tactical-squad   
10    https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminator-squad   
11           https://www.joytoy.com/products/adeptus-custodes-solar-watch-custodian-guard   
12              https://www.joytoy.com/products/imperial-fists-mklll-breacher-legionaries   
13                     https://www.joytoy.com/products/dark-angels-deathwing-knight-squad   
14                    https://www.joytoy.com/products/dark-angels-deathwing-action-figure   
15             https://www.joytoy.com/products/imperial-fists-mklll-despoiler-legionaries   
16               https://www.joytoy.com/products/imperial-fists-mklli-tacticallegionaries   
17                              https://www.joytoy.com/products/grey-knights-strike-squad   
18                         https://www.joytoy.com/products/grey-knights-interceptor-squad   
19                 https://www.joytoy.com/products/black-templars-primaris-sword-brethren   
20  https://www.joytoy.com/products/ultramarines-desolation-sergeant-with-vengor-launcher   
21              https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran   
0                           https://www.joytoy.com/products/ultramarines-terminator-squad   
1                                    https://www.joytoy.com/products/blood-angels-veteran   
6                    https://www.joytoy.com/products/space-marines-space-wolves-claw-pack   
7                https://www.joytoy.com/products/sons-of-horus-justaerin-terminator-squad   
8                       https://www.joytoy.com/products/sons-of-horus-mkiv-tactical-squad   
9                       https://www.joytoy.com/products/sons-of-horus-mkvi-tactical-squad   
10    https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminat

In [28]:
#Создаем столбец с целевой ссылкой для парсинга каждой модели
static_value = '?VariantsId=' #гет параметр карточки

# Создаем новый столбец, объединяя значения из двух столбцов и текстовое статичное значение
union_cardspositions['full_link'] = union_cardspositions['card_link'].astype(str) + static_value + union_cardspositions['variant_id'].astype(str)
union_cardspositions

card_link  \
0                           https://www.joytoy.com/products/ultramarines-terminator-squad   
1                                    https://www.joytoy.com/products/blood-angels-veteran   
6                    https://www.joytoy.com/products/space-marines-space-wolves-claw-pack   
7                https://www.joytoy.com/products/sons-of-horus-justaerin-terminator-squad   
8                       https://www.joytoy.com/products/sons-of-horus-mkiv-tactical-squad   
9                       https://www.joytoy.com/products/sons-of-horus-mkvi-tactical-squad   
10    https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminator-squad   
11           https://www.joytoy.com/products/adeptus-custodes-solar-watch-custodian-guard   
12              https://www.joytoy.com/products/imperial-fists-mklll-breacher-legionaries   
13                     https://www.joytoy.com/products/dark-angels-deathwing-knight-squad   
14                    https://www.joytoy.com/products/dark-angels-deathwing-action-figure   
15             https://www.joytoy.com/products/imperial-fists-mklll-despoiler-legionaries   
16               https://www.joytoy.com/products/imperial-fists-mklli-tacticallegionaries   
17                              https://www.joytoy.com/products/grey-knights-strike-squad   
18                         https://www.joytoy.com/products/grey-knights-interceptor-squad   
19                 https://www.joytoy.com/products/black-templars-primaris-sword-brethren   
20  https://www.joytoy.com/products/ultramarines-desolation-sergeant-with-vengor-launcher   
21              https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran   
0                           https://www.joytoy.com/products/ultramarines-terminator-squad   
1                                    https://www.joytoy.com/products/blood-angels-veteran   
6                    https://www.joytoy.com/products/space-marines-space-wolves-claw-pack   
7                https://www.joytoy.com/products/sons-of-horus-justaerin-terminator-squad   
8                       https://www.joytoy.com/products/sons-of-horus-mkiv-tactical-squad   
9                       https://www.joytoy.com/products/sons-of-horus-mkvi-tactical-squad   
10    https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminator-squad   
11           https://www.joytoy.com/products/adeptus-custodes-solar-watch-custodian-guard   
12              https://www.joytoy.com/products/imperial-fists-mklll-breacher-legionaries   
13                     https://www.joytoy.com/products/dark-angels-deathwing-knight-squad   
14                    https://www.joytoy.com/products/dark-angels-deathwing-action-figure   
15             https://www.joytoy.com/products/imperial-fists-mklll-despoiler-legionaries   
16               https://www.joytoy.com/products/imperial-fists-mklli-tacticallegionaries   
17                              https://www.joytoy.com/products/grey-knights-strike-squad   
18                         https://www.joytoy.com/products/grey-knights-interceptor-squad   
19                 https://www.joytoy.com/products/black-templars-primaris-sword-brethren   
20  https://www.joytoy.com/products/ultramarines-desolation-sergeant-with-vengor-launcher   
21              https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran   
0                           https://www.joytoy.com/products/ultramarines-terminator-squad   
1                                    https://www.joytoy.com/products/blood-angels-veteran   
6                    https://www.joytoy.com/products/space-marines-space-wolves-claw-pack   
7                https://www.joytoy.com/products/sons-of-horus-justaerin-terminator-squad   
8                       https://www.joytoy.com/products/sons-of-horus-mkiv-tactical-squad   
9                       https://www.joytoy.com/products/sons-of-horus-mkvi-tactical-squad   
10    https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminat

In [29]:
#for index, row_value in enumerate(union_cardspositions['full_link']):
    # Формируем URL, используя значение из full_link
 #   url = row_value

    # Отправляем запрос к URL
  #  try:
   #     response = requests.get(url)
        # Обработка полученного ответа response
        # Например, вывод статуса ответа
     #   print(f"Статус запроса к {url}: {response.status_code}")
    #except Exception as e:
      #  break

In [30]:
# Для теста
#union_cardspositions2 = {
#    'full_link': ['https://www.joytoy.com/products/imperial-fists-legion-cataphractii-terminator-squad?VariantsId=10064']}

#union_cardspositions2 = pd.DataFrame(union_cardspositions2)

In [31]:
#union_cardspositions2

In [32]:
#Начинаем парсить каждую из карточек
#union_cardspositions2['all_img_card'] = ''

#for index, row_value in enumerate(union_cardspositions2['full_link']):
    # Формируем URL, используя значение из full_link

    # Отправляем запрос к URL
  #  url = row_value
   # text_card = requests.get(url)

    # Проверяем успешность запроса
    #if text_card.status_code == 200:
        # Используем BeautifulSoup для парсинга HTML
     #   soup = BeautifulSoup(text_card.text, 'html.parser')

        # Находим нужные данные в HTML-коде, например, значение атрибута src
      #  images = soup.find_all('img', class_='thumb_video_pic thumb_big_pic lazyloaded')   #[0].find_all('img')
       # if images:
            # для получения значений атрибута src для всех изображений
        #    img_values = [img.get('src') for img in images]
            #my_string_src_values = ', '.join(img_values) # используем метод джоин для для перевода листа img_values в строку
            #src_values_format = my_string_src_values.replace(', ', ' | ') # заменяем символ в строке
            # Сохраняем результат в union_cardspositions
         #   union_cardspositions2.at[index, 'all_img_card2'] = src_values_format
        #else:
            # Если теги img не найдены, можно установить другое значение по умолчанию
         #   union_cardspositions2.at[index, 'all_img_card2'] = 'Not Found'
    #else:
        # Если запрос не успешен, можно установить другое значение по умолчанию
        #union_cardspositions2.at[index, 'all_img_card2'] = 'Request Failed'

# Выводим результаты
#union_cardspositions2.index.name = '№'
#pd.set_option('display.max_colwidth', None)
#pd.set_option('display.max_rows', None)
#union_cardspositions2

In [33]:
#Берем в датафрейм только ссылки
filtered_df_img = filtered_df[['all_img_card']]
filtered_df_img  = filtered_df_img[filtered_df_img['all_img_card'].str.contains('.jpg', case=False)]
filtered_df_img

all_img_card
№                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            
4                                                                                                                                                                                                                                                                                   https://img.joytoy.com/u_file/2404/04/photo/262A7740.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7741.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7711.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7712.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7710.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7726.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7727.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7751.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7720.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7721.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7724.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7725.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7739.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7752.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7731.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7732.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7734.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7736.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7737.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7753.jpg
5                                                                                                                                                                                                                                                                                 https://img.joytoy.com/u_file/2404/03/photo/B-04bb.jpg | https://img.joytoy.com/u_file/2404/03/photo/2-d51c.jpg | https://img.joytoy.com/u_file/2404/03/photo/3.jpg | https://img.joytoy.com/u_file/2404/03/photo/4-e32a.jpg | https://img.joytoy.com/u_file/2404/03/photo/5.jpg | https://img.joytoy.com/u_file/2404/03/photo/6.jpg | https://img.joytoy.com/u_file/2404/03/photo/2-7c25.jpg | https://img.joytoy.com/u_file/2404/03/photo/3-c7bd.jpg | https://img.joytoy.com/u_file/2404/03/photo/4-9288.jpg | https://img.joytoy.com/u_file/2404/03/photo/5-caba.jpg | https://img.joytoy.com/u_file/2404/03/photo/6-2541.jpg | https://img.joytoy.com/u_file/2404/03/photo/2-204a.jpg | https://img.joytoy.com/u_file/2404/03/photo/3-efc8.jpg | https://img.joytoy.com/u_file/2404/03/photo/4-0f75.jpg | https://img.joytoy.com

In [34]:
links_list = filtered_df_img['all_img_card'].str.strip().str.split('|').tolist()

# Создание нового DataFrame из списка ссылок
filtered_df_img2 = pd.DataFrame({'all_img_card': links_list})
filtered_df_img2

all_img_card
0                                                                                                                                                                                                                                                                                      [https://img.joytoy.com/u_file/2404/04/photo/262A7740.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7741.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7711.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7712.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7710.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7726.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7727.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7751.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7720.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7721.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7724.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7725.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7739.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7752.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7731.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7732.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7734.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7736.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7737.jpg ,  https://img.joytoy.com/u_file/2404/04/photo/262A7753.jpg]
1                                                                                                                                                                                                                                                                                   [https://img.joytoy.com/u_file/2404/03/photo/B-04bb.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/2-d51c.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/3.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/4-e32a.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/5.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/6.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/2-7c25.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/3-c7bd.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/4-9288.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/5-caba.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/6-2541.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/2-204a.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/3-efc8.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/4-0f75.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/5-64e2.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/6-8e94.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/2-1bab.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/3-7d89.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/4-90e9.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/5-c7c9.jpg ,  https://img.joytoy.com/u_file/2404/03/photo/6-ac37.jpg]
2                                                                                                                            [https://img.joytoy.com/u_file/2403/25/photo/1-3.jpg ,  https://img.joytoy.com/u_file/2403/25/photo/2.jpg ,  https://img.joytoy.com/u_file/2403/25/photo/7.jpg ,  https://img.joytoy.com/u_file/2403/25/photo/4.jpg ,  https://img.joytoy.com/u_file/2403/25/photo/6.jpg ,  https://img.joytoy.com/u_file/2403/25/photo/8.jpg ,  https://img.joytoy.com/u_file/2403/25/photo/4-845c.jpg ,  https://img.joytoy.com/u_file/2403/25/photo/7-1c07.jpg ,  https://img.joytoy.com/u_file/2403/25/photo/2-d5ef.jpg ,  https://img.joytoy.com/u_file/2403/25/photo/5.jpg ,  https://img.joytoy.com/u_file/2403/25/photo/6-e6d4.jpg ,  https://img.joytoy.com/u_file/2403/25/photo/8-6603.jpg ,  https://img.joytoy.com/u_file/2403/25/photo/2-7a24.jpg ,  https://img.joytoy.com/u_file/2403/25/photo/3.jpg ,  https://img.joytoy.com/u_file/2403/25/photo/4-7799.jpg ,  https://img.joytoy.com/u_file/2403/25/photo/5-96e8.jpg ,  https://img.joy

In [35]:
img_data = []

for row_index, row in filtered_df_img2.iterrows():
    for item in row['all_img_card']:
        img_data.append({'links': item})

df_img_link = pd.DataFrame(img_data)

In [36]:
#Выбор количество картинов для последующего датафрейма
df_img_link2 = df_img_link #[3:20] #Убрать условие для полной выборки
df_img_link2

links
0           https://img.joytoy.com/u_file/2404/04/photo/262A7740.jpg 
1           https://img.joytoy.com/u_file/2404/04/photo/262A7741.jpg 
2           https://img.joytoy.com/u_file/2404/04/photo/262A7711.jpg 
3           https://img.joytoy.com/u_file/2404/04/photo/262A7712.jpg 
4           https://img.joytoy.com/u_file/2404/04/photo/262A7710.jpg 
5           https://img.joytoy.com/u_file/2404/04/photo/262A7726.jpg 
6           https://img.joytoy.com/u_file/2404/04/photo/262A7727.jpg 
7           https://img.joytoy.com/u_file/2404/04/photo/262A7751.jpg 
8           https://img.joytoy.com/u_file/2404/04/photo/262A7720.jpg 
9           https://img.joytoy.com/u_file/2404/04/photo/262A7721.jpg 
10          https://img.joytoy.com/u_file/2404/04/photo/262A7724.jpg 
11          https://img.joytoy.com/u_file/2404/04/photo/262A7725.jpg 
12          https://img.joytoy.com/u_file/2404/04/photo/262A7739.jpg 
13          https://img.joytoy.com/u_file/2404/04/photo/262A7752.jpg 
14          https://img.joytoy.com/u_file/2404/04/photo/262A7731.jpg 
15          https://img.joytoy.com/u_file/2404/04/photo/262A7732.jpg 
16          https://img.joytoy.com/u_file/2404/04/photo/262A7734.jpg 
17          https://img.joytoy.com/u_file/2404/04/photo/262A7736.jpg 
18          https://img.joytoy.com/u_file/2404/04/photo/262A7737.jpg 
19           https://img.joytoy.com/u_file/2404/04/photo/262A7753.jpg
20            https://img.joytoy.com/u_file/2404/03/photo/B-04bb.jpg 
21            https://img.joytoy.com/u_file/2404/03/photo/2-d51c.jpg 
22                 https://img.joytoy.com/u_file/2404/03/photo/3.jpg 
23            https://img.joytoy.com/u_file/2404/03/photo/4-e32a.jpg 
24                 https://img.joytoy.com/u_file/2404/03/photo/5.jpg 
25                 https://img.joytoy.com/u_file/2404/03/photo/6.jpg 
26            https://img.joytoy.com/u_file/2404/03/photo/2-7c25.jpg 
27            https://img.joytoy.com/u_file/2404/03/photo/3-c7bd.jpg 
28            https://img.joytoy.com/u_file/2404/03/photo/4-9288.jpg 
29            https://img.joytoy.com/u_file/2404/03/photo/5-caba.jpg 
30            https://img.joytoy.com/u_file/2404/03/photo/6-2541.jpg 
31            https://img.joytoy.com/u_file/2404/03/photo/2-204a.jpg 
32            https://img.joytoy.com/u_file/2404/03/photo/3-efc8.jpg 
33            https://img.joytoy.com/u_file/2404/03/photo/4-0f75.jpg 
34            https://img.joytoy.com/u_file/2404/03/photo/5-64e2.jpg 
35            https://img.joytoy.com/u_file/2404/03/photo/6-8e94.jpg 
36            https://img.joytoy.com/u_file/2404/03/photo/2-1bab.jpg 
37            https://img.joytoy.com/u_file/2404/03/photo/3-7d89.jpg 
38            https://img.joytoy.com/u_file/2404/03/photo/4-90e9.jpg 
39            https://img.joytoy.com/u_file/2404/03/photo/5-c7c9.jpg 
40             https://img.joytoy.com/u_file/2404/03/photo/6-ac37.jpg
41               https://img.joytoy.com/u_file/2403/25/photo/1-3.jpg 
42                 https://img.joytoy.com/u_file/2403/25/photo/2.jpg 
43                 https://img.joytoy.com/u_file/2403/25/photo/7.jpg 
44                 https://img.joytoy.com/u_file/2403/25/photo/4.jpg 
45                 https://img.joytoy.com/u_file/2403/25/photo/6.jpg 
46                 https://img.joytoy.com/u_file/2403/25/photo/8.jpg 
47            https://img.joytoy.com/u_file/2403/25/photo/4-845c.jpg 
48            https://img.joytoy.com/u_file/2403/25/photo/7-1c07.jpg 
49            https://img.joytoy.com/u_file/2403/25/photo/2-d5ef.jpg 
50                 https://img.joytoy.com/u_file/2403/25/photo/5.jpg 
51            https://img.joytoy.com/u_file/2403/25/photo/6-e6d4.jpg 
52            https://img.joytoy.com/u_file/2403/25/photo/8-6603.jpg 
53            https://img.joytoy.com/u_file/2403/25/photo/2-7a24.jpg 
54                 https://img.joytoy.com/u_file/2403/25/photo/3.jpg 
55            https://img.joytoy.com/u_file/2403/25/photo/4-7799.jpg 
56            https://img.joytoy.com/u_file/2403/25/photo/5-96e8.jpg 
57  

In [42]:
#Формирование датафрейма с распознанными названиями картинок

text_info6 = []

for link in df_img_link2['links']:
    try:
        # Загружаем изображение из URL и получаем содержимое ответа
        response = requests.get(link.strip())
        response.raise_for_status()

        # Создаем объект Image из байтового содержимого
        image = Image.open(BytesIO(response.content))
        reader = easyocr.Reader(['en'])
        # Применяем функцию readtext() к изображению
        result = reader.readtext(image)
        text_info6.append([entry[1] for entry in result])
    except Exception as e:
        print(f"Error processing image from {link}: {e}")
text_info6

Progress: |██████████████████████████████████████████████████| 100.0% Complete

Progress: |██████████████████████████████████████████████████| 100.0% Complete

[['Ukramtrines',
  'Termanate Squad',
  '#net',
  '#iarej M',
  'Joytoy',
  'MARTAMMER',
  'Oul',
  'MoeataJens',
  'Ilcuirut 5u',
  'Hetonia'],
 ['Ukramtrines',
  'Terminato Squad',
  '#nat',
  '#iarej M',
  'Joytoy',
  'WARRAMMER',
  'DEem reene',
  '[eatnJets',
  'WIeGEtuuEt'],
 ['Ultramarines',
  'Terminator Squad',
  'Sergeant with Power Sword and Teleport Homer',
  'tREE E',
  "126'] MA",
  'Acraej6it(+127/138014+',
  'JOYTOY',
  'X',
  'WARHAMMER',
  '40.000',
  '14.3cm action figure with articulated joints',
  '14.3@*0w3 #tR4uItA ',
  'DeeicsEY'],
 ['Ultramarines',
  'Terminator Squad',
  'Sergeant with Power Sword and Teleport Homer',
  'tREE E',
  "12#'] MA",
  'Acraej6it(+127/138014+',
  'JOYTOY',
  'X',
  'WARHAMMER',
  '40.000',
  '14.3cm action figure with articulated joints',
  '14.3m*0w3 #tR4uItA ',
  'BeeicsEY'],
 ['Ultramarines',
  'Terminator Squad',
  'Sergeant with Power Sword and Teleport Homer',
  '#FREE E',
  "221'] MA",
  'Acraej6it(+127/138014+',
  'JOYTOY',
 

In [43]:
# Создаем датафрейм общий датафрейм

df_img_link2['text_info'] = text_info6

df_img_link2['text_info'] = df_img_link2['text_info'].astype(str)


split_values = df_img_link2['text_info'].str.split(', ')

# Создание новых столбцов со вторым и третьим значениями
df_img_link2['second_value'] = split_values.str[1].str.replace("'", "")
df_img_link2['Product Name'] = split_values.str[2].str.replace("'", "")

df_img_link2


links  \
0           https://img.joytoy.com/u_file/2404/04/photo/262A7740.jpg    
1           https://img.joytoy.com/u_file/2404/04/photo/262A7741.jpg    
2           https://img.joytoy.com/u_file/2404/04/photo/262A7711.jpg    
3           https://img.joytoy.com/u_file/2404/04/photo/262A7712.jpg    
4           https://img.joytoy.com/u_file/2404/04/photo/262A7710.jpg    
5           https://img.joytoy.com/u_file/2404/04/photo/262A7726.jpg    
6           https://img.joytoy.com/u_file/2404/04/photo/262A7727.jpg    
7           https://img.joytoy.com/u_file/2404/04/photo/262A7751.jpg    
8           https://img.joytoy.com/u_file/2404/04/photo/262A7720.jpg    
9           https://img.joytoy.com/u_file/2404/04/photo/262A7721.jpg    
10          https://img.joytoy.com/u_file/2404/04/photo/262A7724.jpg    
11          https://img.joytoy.com/u_file/2404/04/photo/262A7725.jpg    
12          https://img.joytoy.com/u_file/2404/04/photo/262A7739.jpg    
13          https://img.joytoy.com/u_file/2404/04/photo/262A7752.jpg    
14          https://img.joytoy.com/u_file/2404/04/photo/262A7731.jpg    
15          https://img.joytoy.com/u_file/2404/04/photo/262A7732.jpg    
16          https://img.joytoy.com/u_file/2404/04/photo/262A7734.jpg    
17          https://img.joytoy.com/u_file/2404/04/photo/262A7736.jpg    
18          https://img.joytoy.com/u_file/2404/04/photo/262A7737.jpg    
19           https://img.joytoy.com/u_file/2404/04/photo/262A7753.jpg   
20            https://img.joytoy.com/u_file/2404/03/photo/B-04bb.jpg    
21            https://img.joytoy.com/u_file/2404/03/photo/2-d51c.jpg    
22                 https://img.joytoy.com/u_file/2404/03/photo/3.jpg    
23            https://img.joytoy.com/u_file/2404/03/photo/4-e32a.jpg    
24                 https://img.joytoy.com/u_file/2404/03/photo/5.jpg    
25                 https://img.joytoy.com/u_file/2404/03/photo/6.jpg    
26            https://img.joytoy.com/u_file/2404/03/photo/2-7c25.jpg    
27            https://img.joytoy.com/u_file/2404/03/photo/3-c7bd.jpg    
28            https://img.joytoy.com/u_file/2404/03/photo/4-9288.jpg    
29            https://img.joytoy.com/u_file/2404/03/photo/5-caba.jpg    
30            https://img.joytoy.com/u_file/2404/03/photo/6-2541.jpg    
31            https://img.joytoy.com/u_file/2404/03/photo/2-204a.jpg    
32            https://img.joytoy.com/u_file/2404/03/photo/3-efc8.jpg    
33            https://img.joytoy.com/u_file/2404/03/photo/4-0f75.jpg    
34            https://img.joytoy.com/u_file/2404/03/photo/5-64e2.jpg    
35            https://img.joytoy.com/u_file/2404/03/photo/6-8e94.jpg    
36            https://img.joytoy.com/u_file/2404/03/photo/2-1bab.jpg    
37            https://img.joytoy.com/u_file/2404/03/photo/3-7d89.jpg    
38            https://img.joytoy.com/u_file/2404/03/photo/4-90e9.jpg    
39            https://img.joytoy.com/u_file/2404/03/photo/5-c7c9.jpg    
40             https://img.joytoy.com/u_file/2404/03/photo/6-ac37.jpg   
41               https://img.joytoy.com/u_file/2403/25/photo/1-3.jpg    
42                 https://img.joytoy.com/u_file/2403/25/photo/2.jpg    
43                 https://img.joytoy.com/u_file/2403/25/photo/7.jpg    
44                 https://img.joytoy.com/u_file/2403/25/photo/4.jpg    
45                 https://img.joytoy.com/u_file/2403/25/photo/6.jpg    
46                 https://img.joytoy.com/u_file/2403/25/photo/8.jpg    
47            https://img.joytoy.com/u_file/2403/25/photo/4-845c.jpg    
48            https://img.joytoy.com/u_file/2403/25/photo/7-1c07.jpg    
49            https://img.joytoy.com/u_file/2403/25/photo/2-d5ef.jpg    
50                 https://img.joytoy.com/u_file/2403/25/photo/5.jpg    
51            https://img.joytoy.com/u_file/2403/25/photo/6-e6d4.jpg    
52            https://img.joytoy.com/u_file/2403/25/photo/8-6603.jpg    
53            https://img.joytoy.com/u_file/2403/25/photo/2-7a24.jpg    
54                 https://img.joytoy.com/u_file/

**Для позиций типа Veteran Laenatus Vinga etc	https://img.joytoy.com/u_file/2404/03/photo/3.jpg необходмо отфильтровывать и запустить второе обогащение**

In [45]:
test_merge = df_img_link2.merge(cards_position_df, on=["Product Name"])
test_merge

links  \
0           https://img.joytoy.com/u_file/2404/04/photo/262A7711.jpg    
1           https://img.joytoy.com/u_file/2404/04/photo/262A7712.jpg    
2           https://img.joytoy.com/u_file/2404/04/photo/262A7710.jpg    
3           https://img.joytoy.com/u_file/2404/04/photo/262A7751.jpg    
4           https://img.joytoy.com/u_file/2404/04/photo/262A7720.jpg    
5           https://img.joytoy.com/u_file/2404/04/photo/262A7721.jpg    
6           https://img.joytoy.com/u_file/2404/04/photo/262A7724.jpg    
7           https://img.joytoy.com/u_file/2404/04/photo/262A7725.jpg    
8           https://img.joytoy.com/u_file/2404/04/photo/262A7739.jpg    
9           https://img.joytoy.com/u_file/2404/04/photo/262A7752.jpg    
10          https://img.joytoy.com/u_file/2404/04/photo/262A7731.jpg    
11          https://img.joytoy.com/u_file/2404/04/photo/262A7732.jpg    
12          https://img.joytoy.com/u_file/2404/04/photo/262A7734.jpg    
13          https://img.joytoy.com/u_file/2404/04/photo/262A7737.jpg    
14           https://img.joytoy.com/u_file/2404/04/photo/262A7753.jpg   
15            https://img.joytoy.com/u_file/2404/03/photo/2-1bab.jpg    
16            https://img.joytoy.com/u_file/2404/03/photo/3-7d89.jpg    
17            https://img.joytoy.com/u_file/2404/03/photo/4-90e9.jpg    
18            https://img.joytoy.com/u_file/2404/03/photo/5-c7c9.jpg    
19             https://img.joytoy.com/u_file/2404/03/photo/6-ac37.jpg   
20            https://img.joytoy.com/u_file/2403/25/photo/4-845c.jpg    
21            https://img.joytoy.com/u_file/2403/25/photo/7-1c07.jpg    
22            https://img.joytoy.com/u_file/2403/25/photo/2-d5ef.jpg    
23                 https://img.joytoy.com/u_file/2403/25/photo/5.jpg    
24            https://img.joytoy.com/u_file/2403/25/photo/6-e6d4.jpg    
25            https://img.joytoy.com/u_file/2403/25/photo/8-6603.jpg    
26            https://img.joytoy.com/u_file/2403/25/photo/2-7a24.jpg    
27                 https://img.joytoy.com/u_file/2403/25/photo/3.jpg    
28            https://img.joytoy.com/u_file/2403/25/photo/4-7799.jpg    
29            https://img.joytoy.com/u_file/2403/25/photo/5-96e8.jpg    
30            https://img.joytoy.com/u_file/2403/25/photo/7-6635.jpg    
31            https://img.joytoy.com/u_file/2403/25/photo/8-3a67.jpg    
32            https://img.joytoy.com/u_file/2403/25/photo/4-f6f1.jpg    
33            https://img.joytoy.com/u_file/2403/25/photo/5-8620.jpg    
34            https://img.joytoy.com/u_file/2403/25/photo/2-c474.jpg    
35            https://img.joytoy.com/u_file/2403/25/photo/3-f595.jpg    
36            https://img.joytoy.com/u_file/2403/25/photo/6-2309.jpg    
37             https://img.joytoy.com/u_file/2403/25/photo/8-22a3.jpg   
38     https://img.joytoy.com/u_file/2403/05/photo/DSC04288-f525.jpg    
39     https://img.joytoy.com/u_file/2403/05/photo/DSC04290-f740.jpg    
40          https://img.joytoy.com/u_file/2403/05/photo/DSC04291.jpg    
41     https://img.joytoy.com/u_file/2403/05/photo/DSC04320-e29c.jpg    
42     https://img.joytoy.com/u_file/2403/05/photo/DSC04249-f817.jpg    
43     https://img.joytoy.com/u_file/2403/05/photo/DSC04254-aeaf.jpg    
44     https://img.joytoy.com/u_file/2403/05/photo/DSC04257-5586.jpg    
45     https://img.joytoy.com/u_file/2403/05/photo/DSC04317-3917.jpg    
46     https://img.joytoy.com/u_file/2403/05/photo/DSC04273-0e70.jpg    
47     https://img.joytoy.com/u_file/2403/05/photo/DSC04277-cee1.jpg    
48     https://img.joytoy.com/u_file/2403/05/photo/DSC04281-eb9f.jpg    
49      https://img.joytoy.com/u_file/2403/05/photo/DSC04319-7cd4.jpg   
50          https://img.joytoy.com/u_file/2402/29/photo/262A7488.jpg    
51          https://img.joytoy.com/u_file/2402/29/photo/262A7488.jpg    
52          https://img.joytoy.com/u_file/2402/29/photo/262A7489.jpg    
53          https://img.joytoy.com/u_file/2402/29/photo/262A7489.jpg    
54          https://img.joytoy.com/u_file/2402/29

In [46]:
result_test_merge = test_merge.groupby('Product Name')['links'].unique().reset_index()

result_test_merge

Product Name  \
0                                                     Alberic   
1                                                    Alberigo   
2                                              Brother Gunnar   
3                                                Brother Olaf   
4                                            Brother Torrvald   
5                         Custodian Guard with Guardian Spear   
6   Custodian Guard with Sentinel Blade and Praesidium Shield   
7                                                  Granbertus   
8                                  Grey Knight with Psilencer   
9                                  Grey Knight with Psycannon   
10                                                    Harmund   
11                                       Interceptor Justicar   
12                               Interceptor with Incinerator   
13      Interceptor with Storm Bolter and Nemesis Force Sword   
14                             Justaerin with Lightning Claws   
15                  Justaerin with Multi-melta and Power Maul   
16                              Justaerin with Thunder Hammer   
17                                                   Justicar   
18                          Legion Breacher with Graviton Gun   
19                             Legion Breacher with Lascutter   
20              Legion Cataphractii Sergeant with Power Sword   
21                           Legion Despoiler with Chainsword   
22                                      Legionary with Bolter   
23                         Legionary with Bolter & Chainblade   
24                                      Legionary with Flamer   
25                              Legionary with Legion Vexilla   
26                                  Legionary with Nuncio Vox   
27                                Sergeant with Plasma Pistol   
28                                   Sergeant with Power Fist   
29                                  Sergeant with Power Sword   
30               Sergeant with Power Sword and Teleport Homer   
31                               Sergeant with Thunder Hammer   
32                             Terminator with Assault Cannon   
33                               Terminator with Storm Bolter   
34                                            Vexilus Praetor   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   links  
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              [ 

In [47]:
result_test_merge = test_merge.groupby(['Product Name', 'Price', 'SKU', 'VariantsId']).agg({'links': list}).reset_index()
result_test_merge1 = result_test_merge.rename(columns={'VariantsId': 'variant_id'})

result_test_merge1['variant_id'] = result_test_merge1['variant_id'].str.replace(r' ', '', regex=True).astype(str)

result_test_merge1

Product Name  Price  \
0                                                     Alberic  42.99   
1                                                    Alberigo  32.99   
2                                              Brother Gunnar  32.99   
3                                                Brother Olaf  32.99   
4                                            Brother Torrvald  32.99   
5                         Custodian Guard with Guardian Spear  44.99   
6   Custodian Guard with Sentinel Blade and Praesidium Shield  44.99   
7                                                  Granbertus  42.99   
8                                  Grey Knight with Psilencer  46.99   
9                                  Grey Knight with Psycannon  46.99   
10                                                    Harmund  42.99   
11                                       Interceptor Justicar  49.99   
12                               Interceptor with Incinerator  46.99   
13      Interceptor with Storm Bolter and Nemesis Force Sword  46.99   
14                             Justaerin with Lightning Claws  57.99   
15                  Justaerin with Multi-melta and Power Maul  57.99   
16                              Justaerin with Thunder Hammer  57.99   
17                                                   Justicar  49.99   
18                          Legion Breacher with Graviton Gun  46.99   
19                             Legion Breacher with Lascutter  46.99   
20              Legion Cataphractii Sergeant with Power Sword  57.99   
21                           Legion Despoiler with Chainsword  43.99   
22                                      Legionary with Bolter  43.99   
23                                      Legionary with Bolter  43.99   
24                         Legionary with Bolter & Chainblade  41.99   
25                                      Legionary with Flamer  43.99   
26                              Legionary with Legion Vexilla  43.99   
27                              Legionary with Legion Vexilla  46.99   
28                              Legionary with Legion Vexilla  46.99   
29                                  Legionary with Nuncio Vox  41.99   
30                                Sergeant with Plasma Pistol  43.99   
31                                   Sergeant with Power Fist  43.99   
32                                   Sergeant with Power Fist  46.99   
33                                  Sergeant with Power Sword  43.99   
34                                  Sergeant with Power Sword  46.99   
35               Sergeant with Power Sword and Teleport Homer  57.99   
36                               Sergeant with Thunder Hammer  46.99   
37                             Terminator with Assault Cannon  54.99   
38                               Terminator with Storm Bolter  54.99   
39                                            Vexilus Praetor  44.99   

              SKU variant_id  \
0   6973130373822      10025   
1   6973130373372      10118   
2   6973130372719      10097   
3   6973130372726      10098   
4   6973130372733      10099   
5   6973130379336      10058   
6   6973130379343      10057   
7   6973130373839      10027   
8   6973130379008      10034   
9   6973130379015      10035   
10  6973130373846      10026   
11  6973130378964      10029   
12  6973130378971      10030   
13  6973130378988      10031   
14  6973130379725      10092   
15  6973130379749      10094   
16  6973130379732      10093   
17  6973130378995      10033   
18  6973130379114      10054   
19  6973130379121      10055   
20  6973130379374      10061   
21  6973130379091      10043   
22  6973130379077      10040   
23  6973130379602      10089   
24  6973130379497      10069   
25  6973130379596      10088   
26  6973130379480      10067   
27  6973130379053      10038   
28  6973130379589      10087   
29  6973130379473      10068   
30  6973130379084      10042   
31  6973130379060      10039   
32  6973130379572      10086   
33  6973

In [49]:
result_test_merge1

Product Name  Price  \
0                                                     Alberic  42.99   
1                                                    Alberigo  32.99   
2                                              Brother Gunnar  32.99   
3                                                Brother Olaf  32.99   
4                                            Brother Torrvald  32.99   
5                         Custodian Guard with Guardian Spear  44.99   
6   Custodian Guard with Sentinel Blade and Praesidium Shield  44.99   
7                                                  Granbertus  42.99   
8                                  Grey Knight with Psilencer  46.99   
9                                  Grey Knight with Psycannon  46.99   
10                                                    Harmund  42.99   
11                                       Interceptor Justicar  49.99   
12                               Interceptor with Incinerator  46.99   
13      Interceptor with Storm Bolter and Nemesis Force Sword  46.99   
14                             Justaerin with Lightning Claws  57.99   
15                  Justaerin with Multi-melta and Power Maul  57.99   
16                              Justaerin with Thunder Hammer  57.99   
17                                                   Justicar  49.99   
18                          Legion Breacher with Graviton Gun  46.99   
19                             Legion Breacher with Lascutter  46.99   
20              Legion Cataphractii Sergeant with Power Sword  57.99   
21                           Legion Despoiler with Chainsword  43.99   
22                                      Legionary with Bolter  43.99   
23                                      Legionary with Bolter  43.99   
24                         Legionary with Bolter & Chainblade  41.99   
25                                      Legionary with Flamer  43.99   
26                              Legionary with Legion Vexilla  43.99   
27                              Legionary with Legion Vexilla  46.99   
28                              Legionary with Legion Vexilla  46.99   
29                                  Legionary with Nuncio Vox  41.99   
30                                Sergeant with Plasma Pistol  43.99   
31                                   Sergeant with Power Fist  43.99   
32                                   Sergeant with Power Fist  46.99   
33                                  Sergeant with Power Sword  43.99   
34                                  Sergeant with Power Sword  46.99   
35               Sergeant with Power Sword and Teleport Homer  57.99   
36                               Sergeant with Thunder Hammer  46.99   
37                             Terminator with Assault Cannon  54.99   
38                               Terminator with Storm Bolter  54.99   
39                                            Vexilus Praetor  44.99   

              SKU variant_id  \
0   6973130373822      10025   
1   6973130373372      10118   
2   6973130372719      10097   
3   6973130372726      10098   
4   6973130372733      10099   
5   6973130379336      10058   
6   6973130379343      10057   
7   6973130373839      10027   
8   6973130379008      10034   
9   6973130379015      10035   
10  6973130373846      10026   
11  6973130378964      10029   
12  6973130378971      10030   
13  6973130378988      10031   
14  6973130379725      10092   
15  6973130379749      10094   
16  6973130379732      10093   
17  6973130378995      10033   
18  6973130379114      10054   
19  6973130379121      10055   
20  6973130379374      10061   
21  6973130379091      10043   
22  6973130379077      10040   
23  6973130379602      10089   
24  6973130379497      10069   
25  6973130379596      10088   
26  6973130379480      10067   
27  6973130379053      10038   
28  6973130379589      10087   
29  6973130379473      10068   
30  6973130379084      10042   
31  6973130379060      10039   
32  6973130379572      10086   
33  6973

In [146]:
result_test_merge_full = pd.merge(result_test_merge1, union_cardspositions, left_on='variant_id', right_on='variant_id', how='left')
result_test_merge_full

Product Name  Price  \
0                                                     Alberic  42.99   
1                                                    Alberigo  32.99   
2                                              Brother Gunnar  32.99   
3                                                Brother Olaf  32.99   
4                                            Brother Torrvald  32.99   
5                         Custodian Guard with Guardian Spear  44.99   
6   Custodian Guard with Sentinel Blade and Praesidium Shield  44.99   
7                                                  Granbertus  42.99   
8                                  Grey Knight with Psilencer  46.99   
9                                  Grey Knight with Psycannon  46.99   
10                                                    Harmund  42.99   
11                                       Interceptor Justicar  49.99   
12                               Interceptor with Incinerator  46.99   
13      Interceptor with Storm Bolter and Nemesis Force Sword  46.99   
14                             Justaerin with Lightning Claws  57.99   
15                  Justaerin with Multi-melta and Power Maul  57.99   
16                              Justaerin with Thunder Hammer  57.99   
17                                                   Justicar  49.99   
18                          Legion Breacher with Graviton Gun  46.99   
19                             Legion Breacher with Lascutter  46.99   
20              Legion Cataphractii Sergeant with Power Sword  57.99   
21                           Legion Despoiler with Chainsword  43.99   
22                                      Legionary with Bolter  43.99   
23                                      Legionary with Bolter  43.99   
24                         Legionary with Bolter & Chainblade  41.99   
25                                      Legionary with Flamer  43.99   
26                              Legionary with Legion Vexilla  43.99   
27                              Legionary with Legion Vexilla  46.99   
28                              Legionary with Legion Vexilla  46.99   
29                                  Legionary with Nuncio Vox  41.99   
30                                Sergeant with Plasma Pistol  43.99   
31                                   Sergeant with Power Fist  43.99   
32                                   Sergeant with Power Fist  46.99   
33                                  Sergeant with Power Sword  43.99   
34                                  Sergeant with Power Sword  46.99   
35               Sergeant with Power Sword and Teleport Homer  57.99   
36                               Sergeant with Thunder Hammer  46.99   
37                             Terminator with Assault Cannon  54.99   
38                               Terminator with Storm Bolter  54.99   
39                                            Vexilus Praetor  44.99   

              SKU variant_id  \
0   6973130373822      10025   
1   6973130373372      10118   
2   6973130372719      10097   
3   6973130372726      10098   
4   6973130372733      10099   
5   6973130379336      10058   
6   6973130379343      10057   
7   6973130373839      10027   
8   6973130379008      10034   
9   6973130379015      10035   
10  6973130373846      10026   
11  6973130378964      10029   
12  6973130378971      10030   
13  6973130378988      10031   
14  6973130379725      10092   
15  6973130379749      10094   
16  6973130379732      10093   
17  6973130378995      10033   
18  6973130379114      10054   
19  6973130379121      10055   
20  6973130379374      10061   
21  6973130379091      10043   
22  6973130379077      10040   
23  6973130379602      10089   
24  6973130379497      10069   
25  6973130379596      10088   
26  6973130379480      10067   
27  6973130379053      10038   
28  6973130379589      10087   
29  6973130379473      10068   
30  6973130379084      10042   
31  6973130379060      10039   
32  6973130379572      10086   
33  6973

In [149]:
# Создаем чищаем функцией от лишних символов список ссылок на фото
def list_to_string(lst):
    return ' '.join(lst).strip('[]').replace(' ', '').replace(',', ' | ').replace("'", ' ')

# Применение функции к столбцу
result_test_merge_full['links'] = result_test_merge_full['links'].astype(str).apply(list_to_string)

In [150]:
## Приводим все столбцы к единному формату

# Функция для получения первого значения до разделителя |
def get_first_value(string):
    return string.split('|')[0].strip()
# Применение функции к столбцу
result_test_merge_full['img'] = result_test_merge_full['links'].apply(get_first_value)

In [154]:
# Дропаем лишний столбец variant_id
result_test_merge_full = result_test_merge_full.drop(columns=['variant_id'])


KeyError: "['variant_id'] not found in axis"

In [155]:
# Дропаем лишний столбец card_link
result_test_merge_full = result_test_merge_full.drop(columns=['card_link'])

In [166]:
# Даем идентичное название
result_test_merge_full2 = result_test_merge_full.rename(columns={'links': 'all_img_card', 'full_link': 'card_link', 'Product Name': 'name', 'Price': 'price'})

In [158]:
pd.set_option('display.max_colwidth',140)
result_test_merge_full2[["name", "price", "img", "card_link", "SKU", "all_img_card"]]

name  price  \
0                                                     Alberic  42.99   
1                                                    Alberigo  32.99   
2                                              Brother Gunnar  32.99   
3                                                Brother Olaf  32.99   
4                                            Brother Torrvald  32.99   
5                         Custodian Guard with Guardian Spear  44.99   
6   Custodian Guard with Sentinel Blade and Praesidium Shield  44.99   
7                                                  Granbertus  42.99   
8                                  Grey Knight with Psilencer  46.99   
9                                  Grey Knight with Psycannon  46.99   
10                                                    Harmund  42.99   
11                                       Interceptor Justicar  49.99   
12                               Interceptor with Incinerator  46.99   
13      Interceptor with Storm Bolter and Nemesis Force Sword  46.99   
14                             Justaerin with Lightning Claws  57.99   
15                  Justaerin with Multi-melta and Power Maul  57.99   
16                              Justaerin with Thunder Hammer  57.99   
17                                                   Justicar  49.99   
18                          Legion Breacher with Graviton Gun  46.99   
19                             Legion Breacher with Lascutter  46.99   
20              Legion Cataphractii Sergeant with Power Sword  57.99   
21                           Legion Despoiler with Chainsword  43.99   
22                                      Legionary with Bolter  43.99   
23                                      Legionary with Bolter  43.99   
24                         Legionary with Bolter & Chainblade  41.99   
25                                      Legionary with Flamer  43.99   
26                              Legionary with Legion Vexilla  43.99   
27                              Legionary with Legion Vexilla  46.99   
28                              Legionary with Legion Vexilla  46.99   
29                                  Legionary with Nuncio Vox  41.99   
30                                Sergeant with Plasma Pistol  43.99   
31                                   Sergeant with Power Fist  43.99   
32                                   Sergeant with Power Fist  46.99   
33                                  Sergeant with Power Sword  43.99   
34                                  Sergeant with Power Sword  46.99   
35               Sergeant with Power Sword and Teleport Homer  57.99   
36                               Sergeant with Thunder Hammer  46.99   
37                             Terminator with Assault Cannon  54.99   
38                               Terminator with Storm Bolter  54.99   
39                                            Vexilus Praetor  44.99   

                                                              img  \
0               https://img.joytoy.com/u_file/2311/16/photo/1.jpg   
1          https://img.joytoy.com/u_file/2404/03/photo/2-1bab.jpg   
2          https://img.joytoy.com/u_file/2403/25/photo/4-845c.jpg   
3          https://img.joytoy.com/u_file/2403/25/photo/2-7a24.jpg   
4          https://img.joytoy.com/u_file/2403/25/photo/4-f6f1.jpg   
5         https://img.joytoy.com/u_file/2401/18/photo/A1-1333.jpg   
6              https://img.joytoy.com/u_file/2401/18/photo/A1.jpg   
7          https://img.joytoy.com/u_file/2311/16/photo/1-fa8e.jpg   
8         https://img.joytoy.com/u_file/2312/01/photo/A1-963a.jpg   
9         https://img.joytoy.com/u_file/2312/01/photo/A1-e2ac.jpg   
10         https://img.joytoy.com/u_file/2311/16/photo/1-cb97.jpg   
11        https://img.joytoy.com/u_file/2312/01/photo/A1-732c.jpg   
12        https://img.joytoy.com/u_file/2312/01/photo/A1-ccbb.jpg   
13             https://img.joytoy.com/u_file/2312/01/photo/A2.jpg   
14  https://img.joytoy.com/u_file/2403/05/photo/DSC04288-f525.jpg   


In [161]:
# Выполняем union основного df и нового текущего
union_dfs_final = pd.concat([final_df, result_test_merge_full2])

In [164]:
union_dfs_final = union_dfs_final.drop(columns=['href'])

In [179]:
union_dfs_final

name  \
0                                                        Space Wolves Geigor Fell-Hand   
1                          Space Wolves Contemptor Dreadnought with Gravis Bolt Cannon   
2                                          Ultramarines Librarian in Terminator Armour   
3                                      Ultramarines Terminator Captain Severus Agemman   
4                                                        Ultramarines Terminator Squad   
5                                                                 Blood Angels Veteran   
6                                                 Space Marines Space Wolves Claw Pack   
7                      Sons of Horus Ezekyle Abaddon First Captain of the XVIth Legion   
8                           Sons of Horus Warmaster Horus Primarch of the XVIth Legion   
9                                             Sons of Horus Justaerin Terminator Squad   
10                      Sons of Horus Legion Praetor in Cataphractii Terminator Armour   
11                                                   Sons of Horus MKIV Tactical Squad   
12                         Sons of Horus Contemptor Dreadnought with Gravis Autocannon   
13                                         Sons of Horus Legion Praetor with Power Axe   
14                                                   Sons of Horus MKVI Tactical Squad   
15       Adeptus Custodes Vexilus Praetor in Allarus Terminator Armour Phelam Tolguror   
16                               Adepta Sororitas Penitent Engine with Penitent Flails   
17                                               Imperial Fists Contemptor Dreadnought   
18                                 Imperial Fists Legion Cataphractii Terminator Squad   
19                                                                  Intercessors Group   
20                                        Adeptus Custodes Solar Watch Custodian Guard   
21                                                         Imperial Fists Intercessors   
22                                                           Blood Angels Intercessors   
23                                                           Ultramarines Intercessors   
24                                                           Space Wolves Intercessors   
25                       Imperial Fists Sigismund, First Captain of the lmperial Fists   
26                                           Imperial Fists Mklll Breacher Legionaries   
27                                                          Grey Knights Kaldor Draigo   
28                                                  Dark Angels Deathwing Knight Squad   
29                                                  Dark Angels Deathwing Strikemaster   
30                                                          Imperial Fists Fafnir Rann   
31                                      Imperial Fists Legion Praetor with Power Sword   
32                                          Imperial Fists Mklll Despoiler Legionaries   
33                                           Imperial Fists MkIII Tactical Legionaries   
34                                               Imperial Fists Legion Chaplain Consul   
35                                                           Grey Knights Strike Squad   
36                                                      Grey Knights Interceptor Squad   
37                                                     Adeptus Custodes Blade Champion   
38                       Adeptus Mechanicus Kastelan Robot with Heavy Phosphor Blaster   
39                                            Astra Militarum Cadian Armoured Sentinel   
40                                                       Ultramarines Primaris Captain   
41                                              Black Templars Primaris Sword Brethren   
42                                                    Adepta Sororitas Penitent Engine   
43                                                               Ultramarines Judiciar   
44                              

### **ФИНАЛИЗУРЕМ ВЫГРУЗКУ В G-SHEETS**


In [170]:
# Подключение к Google Таблицам
scope = ['https://www.googleapis.com/auth/spreadsheets',
'https://www.googleapis.com/auth/drive']

In [171]:
# Авторизация пользователя с помощью JSON-ключа
credentials = ServiceAccountCredentials.from_json_keyfile_name('/content/able-engine-276816-f1ea18570bfa.json', scope)
client = gspread.authorize(credentials)

In [172]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [177]:
sheet = client.open('joytoy_parsing_table').add_worksheet(title='joytoy_wh', rows=1, cols=1)
#.add_worksheet(title='joytoy_wh', rows=1, cols=1) для создания нового листа

In [178]:
# Запись датафрейма на ранее созданный лист с сохранением структуры датафрейма
set_with_dataframe(sheet, union_dfs_final)
format_with_dataframe(sheet, union_dfs_final, include_column_header=True)
print('Данные загружены в Google Таблицы')

Данные загружены в Google Таблицы


### **МУСОР**

In [ ]:
image_url = 'https://img.joytoy.com/u_file/2404/04/photo/262A7740.jpg'

# Проверяем доступность ссылки
response = requests.get(image_url)

if response.status_code == 200:
    print("Изображение доступно.")
else:
    print(f"Ошибка: {response.status_code}")

In [ ]:
#Начинаем парсить каждую из карточек
for index, row_value in enumerate(union_cardspositions['full_link']):
    # Формируем URL, используя значение из full_link
    url = row_value

    # Проверяем успешность запроса
    if text_card.status_code == 200:
        # Используем BeautifulSoup для парсинга HTML
        soup = BeautifulSoup(text_card.text, 'html.parser')

        # Находим нужные данные в HTML-коде, например, значение атрибута src
        images = soup.find_all('div', class_='thumb_package')[0].find_all('img')
        if images:
            # для получения значений атрибута src для всех изображений
            img_values = [img.get('src') for img in images]
            #my_string_src_values = ', '.join(img_values) # используем метод джоин для для перевода листа img_values в строку
            src_values_format = my_string_src_values.replace(', ', ' | ') # заменяем символ в строке
            # Сохраняем результат в union_cardspositions
            union_cardspositions.at[index, 'all_img_card'] = src_values_format
        else:
            # Если теги img не найдены, можно установить другое значение по умолчанию
            union_cardspositions.at[index, 'all_img_card'] = 'Not Found'
    else:
        # Если запрос не успешен, можно установить другое значение по умолчанию
        union_cardspositions.at[index, 'all_img_card'] = 'Request Failed'

# Выводим результаты
union_cardspositions.index.name = '№'
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)
union_cardspositions

In [ ]:
#Начинаем парсить каждую из карточек
union_cardspositions2['all_img_card2'] = ''

for index, row_value in enumerate(union_cardspositions2['full_link']):
    # Формируем URL, используя значение из full_link

    # Отправляем запрос к URL
    url = row_value
    text_card = requests.get(url)

    # Проверяем успешность запроса
    if text_card.status_code == 200:
        # Используем BeautifulSoup для парсинга HTML
        soup = BeautifulSoup(text_card.text, 'html.parser')

        # Находим нужные данные в HTML-коде, например, значение атрибута src
        images = soup.find_all('li', class_='thumb_video_pic thumb_big_pic lazyloaded')[0].find_all('img')
        if images:
            # для получения значений атрибута src для всех изображений
            img_values = [img.get('src') for img in images]
            my_string_src_values = ', '.join(img_values) # используем метод джоин для для перевода листа img_values в строку
            src_values_format = my_string_src_values.replace(', ', ' | ') # заменяем символ в строке
            # Сохраняем результат в union_cardspositions
            union_cardspositions2.at[index, 'all_img_card2'] = src_values_format
# Выводим результаты
union_cardspositions2.index.name = '№'
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)
union_cardspositions2

In [ ]:
#Начинаем парсить каждую из карточек
union_cardspositions2['all_img_card2'] = ''

for index, row_value in enumerate(union_cardspositions2['full_link']):
    # Формируем URL, используя значение из full_link

    # Отправляем запрос к URL
    url = row_value
    text_card = requests.get(url)

    img_tags = soup.find_all('img', class_='thumb_video_pic thumb_big_pic lazyloaded')

# Извлечение ссылки на изображение из каждого тега <img> и добавление в список
    image_urls = []
    for img_tag in img_tags:
      image_url = img_tag.get('data-src')
      if image_url:
        image_urls.append(image_url)

# Вывод списка URL изображений
print(image_urls)

In [ ]:
img_tags = soup.find_all('div', class_='thumb_video_pic thumb_big_pic lazyloaded')

img_tags

In [ ]:
images = soup.find_all('div', class_='thumb_small')[0].find_all('img')

images

In [ ]:
images2 = soup.find_all('div', class_='pic_box ')[0].find_all('img')

images2

In [ ]:
reader = easyocr.Reader(['en'])
result1 = reader.readtext('https://img.joytoy.com/u_file/2404/04/photo/262A7712.jpg')
print(result1)

In [ ]:
reader = easyocr.Reader(['en'])
result = reader.readtext('https://img.joytoy.com/u_file/2404/03/photo/2-d51c.jpg')
print(result)

In [ ]:
result1

In [ ]:
result1

In [ ]:
text_info = [entry[1] for entry in result1]

print(text_info)

In [ ]:
new_values1 = text_info[:1]
new_values1

In [ ]:
new_values2 = text_info[:2]
new_values2

In [ ]:
#soup = BeautifulSoup(html_code, 'html.parser')

# Находим элемент с классом 'thumb_small'
thumb_small_div = soup.find('div', class_='thumb_video_pic thumb_big_pic lazyloaded')

# Находим все теги <img> внутри элемента 'thumb_small'
images = thumb_small_div.find_all('img')

# Получаем значения атрибута src для каждого изображения
image_urls = [img.get('src') for img in images]

In [ ]:
images

In [ ]:
# Функция для добавления значения из 'column1' в список из 'column2'
def add_value_to_list(row):
    row['range_id'].append(row['VariantsId'])   # Добавляем значение из 'column1'
    return row['range_id']

# Применяем функцию к каждой строке DataFrame
cards_position_df2['range_id'] = cards_position_df2.apply(add_value_to_list, axis=1)

cards_position_df2

In [ ]:
cards_position_df2['range_id'] = [[] for _ in range(len(cards_position_df2))]

# Добавляем значения из 'column1' в списки 'column2'
for index, row in cards_position_df2.iterrows():
    cards_position_df2.at[index, 'range_id'].append(row['max_variantid'])



In [ ]:
cards_position_df2

In [ ]:
data_str = {
    'set of 3': [['166.99', '197', '1.05', 'ZH233047', '0.00', '4142', '10126', '0', '1']],
    'Sergeant with Power Sword and Teleport Homer': [['57.99', '197', '0.35', '6973130379923', '0.00', '4144', '10127', '0', '0']],
    'Terminator with Storm Bolter': [['54.99', '198', '0.35', '6973130379930', '0.00', '4150', '10128', '0', '0']],
    'Terminator with Assault Cannon': [['54.99', '198', '0.35', '6973130379947', '0.00', '4156', '10129', '0', '0']],
    'Set of 4': [['139.99', '17', '1.05', 'ZH031027', '0.00', '3113', '10020', '0', '1']],
    'Sergeant with Vengor Launcher': [['46.99', '19', '0.35', '6973130378803', '0.00', '3089', '10021', '0', '0']],
    'Castellan Launcher (Superkrak)': [['46.99', '19', '0.35', '6973130378810', '0.00', '3115', '10022', '0', '0']],
    'Castellan Launcher (Superfrag)': [['46.99', '19', '0.35', '6973130378827', '0.00', '3121', '10023', '0', '0']]
}


# Преобразуем в формат, который можно использовать для создания датафрейма
data_list = [{'name': key, 'price': value[0][0], 'SKU': value[0][3], 'VariantsId': value[0][6]} for key, value in data_str.items()]
for item in data_list:
    item['SKU_ZH'] = item['SKU']
#name	price href	img	card_link	SKU	all_img_card

In [ ]:
df = pd.DataFrame(data_list)
df

In [ ]:
# Разделение значений в столбце 'Total' на отдельные столбцы
split_total = result_df['Total'].apply(pd.Series)

# Переименование столбцов по вашим правилам
# Пример:
# Новые имена столбцов
new_columns = {
    'set_of': 'Set Of',
    'sergeant_with': 'Sergeant With',
    'castellan_launcher': 'Castellan Launcher'
    # Добавьте остальные столбцы
}

# Переименование столбцов с учетом правил
split_total = split_total.rename(columns=new_columns)

# Объединение результатов с исходным DataFrame
result_df = pd.concat([result_df, split_total], axis=1)

# Удаление столбца 'Total', если он больше не нужен
result_df = result_df.drop(columns=['Total'])

# Вывод обновленного DataFrame
result_df

In [ ]:
#Транспонируем датасет
transposed_df = result_df.transpose()
transposed_df

In [ ]:
#result_df = result_df[result_df['SKU'].str.contains('ZH', case=False)]
#result_df

In [ ]:
total_row = pd.DataFrame(data)
total_row

In [ ]:
# Создание пустого DataFrame
result_total_data = []

# Итерация по данным и добавление каждого элемента в DataFrame
for item in data:
    result_total_data = result_total_data.append(pd.DataFrame.from_dict(item['Total']), ignore_index=True)

# Вывод DataFrame
print(result_total_data)

In [ ]:
for item in data:
    if 'Total' in item and 'Set of 4' in item['Total'] and isinstance(item['Total']['Set of 4'], list):
        row = ','.join([','.join(inner_list) for inner_list in item['Total']['Set of 4']])
        print(row)
    else:
        print("Отсутствуют данные 'Set of 4' для данного элемента.")

In [ ]:
for index, row_value in enumerate(filtered_df['card_link']):
    # Формируем URL, используя значение из card_link
    url = row_value

    urls = []

    # Отправляем запрос к URL
    response = requests.get(url)

    # Проверяем успешность запроса
    if response.status_code == 200:
        # Используем BeautifulSoup для парсинга HTML
        soup = BeautifulSoup(response.text, 'html.parser')

        # Ищем тег <meta> с атрибутом property="og:url"
        meta_tag = soup.find('meta', property='og:url')

        # Проверяем, найден ли тег
        if meta_tag:
            # Получаем содержимое атрибута content
            url_content = meta_tag.get('content')

            # Добавляем URL в список результатов
            urls.append(url_content)

# Выводим список URL
urls

In [ ]:
meta_tag

In [ ]:
data = {
    'card_link': ['https://www.joytoy.com/products/blood-angels-veteran?VariantsId=10114', 'https://www.joytoy.com/products/ultramarines-terminator-squad?VariantsId=10126', 'https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran?VariantsId=10009'],
    # добавьте другие столбцы, если необходимо
}

# Создание DataFrame
final_df2 = pd.DataFrame(data)

final_df2

In [ ]:
final_df2['SET_CNT'] = ''

for index, row_value in enumerate(final_df2['card_link']):
    # Формируем URL, используя значение из card_link
    url = f'{row_value}'

    # Отправляем запрос к URL
    text_card = requests.get(url)

    # Проверяем успешность запроса
    if text_card.status_code == 200:
        # Используем BeautifulSoup для парсинга HTML
        soup = BeautifulSoup(text_card.text, 'html.parser')

        # Находим нужные данные в HTML-коде, значение атрибута, value
        attr_box_element = soup.find_all('div', class_='btn_attr GoodBorderColor GoodBorderHoverColor')
        if attr_box_element in attr_box_element:
          value =  attr_box_element['value']
          set_value = first_div_tag.get('value')
          # Сохраняем результата в столбец
          final_df2.at[index, 'SET_CNT'] = set_value


In [ ]:
final_df2

In [ ]:
pd.final_df2 = [card_link:'https://www.joytoy.com/products/blood-angels-veteran?VariantsId=10114', 'https://www.joytoy.com/products/ultramarines-terminator-squad?VariantsId=10126,' 'https://www.joytoy.com/products/ultramarines-terminator-captain-severus-agemman']
final_df2

In [ ]:
final_df2 = final_df2[['card_link']]

In [ ]:
url2 = 'https://www.joytoy.com/products/blood-angels-veteran?VariantsId=10114'
response = requests.get(url2)
if response.status_code == 200:
  html_content = response.text
  soup = BeautifulSoup(html_content, 'html.parser')
attr_box_elements = soup.find_all('input', id= 'ext_attr')

attr_box_elements

In [ ]:
total_data = data.get('Total', {})

# Проходимся по каждому элементу внутреннего словаря 'Total'
for key, value in total_data.items():
    # В value у нас список списков. Первый элемент каждого списка содержит цену
    #prices = [item[0] for item in value]
    first_three_values = [item[:7] for item in value]
    print(f"'{key}': {first_three_values}")

In [ ]:
total_data = data.get('Total', {})

# Проходимся по каждому элементу внутреннего словаря 'Total'
for key, value in total_data.items():
    # В value у нас список списков. Первый элемент каждого списка содержит цену
    #prices = [item[0] for item in value]
    first_three_values = [item[:7] for item in value]
    print(f"'{key}': {first_three_values}")

In [ ]:
СОЗДАЕМ ДАТАФРЕЙМ С ЭТИМИ ЗНАЧЕНИЯМ ПЕРЕД СОЗДАНИЕМ И ПАРСИНГА ССЫЛКИ

In [ ]:
for attr_box_element in attr_box_element:
    value =  attr_box_element['value']
    print(value)
    break

In [ ]:
url2 = 'https://www.joytoy.com/products/primaris-space-marines-bladeguard-veteran'
response = requests.get(url2)
if response.status_code == 200:
  html_content = response.text
  soup = BeautifulSoup(html_content, 'html.parser')
input_element = soup.find_all('div', class_ = 'ext_attr')
if input_element:
  # Получаем значение атрибута value
  value = input_element.get('value')
  # Декодируем HTML-сущности в строке
  decoded_value = decode_html_entities(value)
  # Преобразуем строку в объект Python (словарь)
  data = json.loads(decoded_value)
  # Выводим полученные данные
  print(data)

In [ ]:
###Получение последнего символа

attr_box_list = list(attr_box_element)

if attr_box_element:
    # Получаем значение 'value' первого элемента
    value = attr_box_element[0]['value']
    words = value.split()
    last_word2 = words[-1]
else:
    print("Список attr_box_element пуст")

In [ ]:
#Получение последнего значения

words = value.split()

# Получение последнего слова
last_word = words[-1]

last_word

#  ФОРМИРОВАНИЕ ФАЙЛОВ ДЛЯ ИМПОРТА В КАБИНЕТЫ АВИТО И ВК

## **--> ФОРМИРОВАНИЕ ФАЙЛОВ ДЛЯ АВИТО**

**Создаем таблицу для загрузки в АВИТО**

In [163]:
#Создаем ключевые столбцы из парсинга датафрейма
avit_df = final_df[['SKU', 'name', 'all_img_card']]
avit_df[:5]

SKU                                                         name  \
0  6973130379954                                Space Wolves Geigor Fell-Hand   
1  6973130379961  Space Wolves Contemptor Dreadnought with Gravis Bolt Cannon   
2  6973130379794                  Ultramarines Librarian in Terminator Armour   
3  6973130379916              Ultramarines Terminator Captain Severus Agemman   
4       ZH233047                                Ultramarines Terminator Squad   

                                                                                                                                  all_img_card  
0  https://img.joytoy.com/u_file/2404/11/photo/A1-0f48.jpg | https://img.joytoy.com/u_file/2404/11/photo/A2-b7b8.jpg | https://img.joytoy.c...  
1  https://img.joytoy.com/u_file/2404/11/photo/A1-29d2.jpg | https://img.joytoy.com/u_file/2404/11/photo/A2-03e4.jpg | https://img.joytoy.c...  
2  https://img.joytoy.com/u_file/2404/04/photo/F-2.jpg | https://img.joytoy.com/u_file/2404/04/photo/F-3.jpg | https://img.joytoy.com/u_fil...  
3  https://img.joytoy.com/u_file/2404/04/photo/262A7673.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7674.jpg | https://img.joytoy...  
4  https://img.joytoy.com/u_file/2404/04/photo/262A7740.jpg | https://img.joytoy.com/u_file/2404/04/photo/262A7741.jpg | https://img.joytoy...

**Задачем столбцы со статичными значениями**

In [ ]:
Description_string = """
В нaличии. Hовый, запечатанный.

JоyТоy {name}

Oчeнь мнoго пoдвижныx суставов, сoответcтвeннo бoльшой выбop пoз для фигурки - к каждой мoдeли идут дополнительные головы, руки, оружие и т.д.

❤️ Добавь это объявление к себе в избранное

✅ В профиле есть еще очень много интересного!)

Если интересует что-то из Jоytоy Wаrhаmmеr/Infinity/Dаrk Sоursе/LЕGО, пишите - можем привезти под заказ!

# Wаrhаmmеr 40000, Вархаммер 40000, Wаrhаmmеr 40k, JоyТоy, Jоy Тоy, Dеаth Коrрs оf Кriеg, Корпус Смерти Крига, Имперская гвардия, Imреriаl Guаrd, Sрасе Маrinеs, Sрасе Wоlvеs, Ultrаmаrinеs, Ультрамарины, Вlооd Аngеls, Кровавые Ангелы, Аstrа Мilitаrum, Ваха, Коллекционные фигурки"""

#Description_string

#display(avit_df.style.set_properties(subset=[Description_string'], **{'white-space': 'pre-line'}))

In [ ]:
avit_df['AvitoId'], avit_df['AdStatus'], avit_df['Category'], avit_df['GoodsType'],  avit_df['VehicleType'], avit_df['Address'], avit_df['Condition'], avit_df['AdType'], avit_df['ContactPhone'], avit_df['DateBegin'], avit_df['DateEnd'], avit_df['AllowEmail'], avit_df['ManagerName'], avit_df['ImageNames'], avit_df['Description'], avit_df['Price'] = '', 'Free', 'Коллекционирование', 'Модели', '', 'Москва, метро Улица Скобелевская', 'Новое', 'Продаю своё', '+7 985 182-56-36', '', '', '', '', '', Description_string, ''

<ipython-input-30-d66c6d39393a>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  avit_df['AvitoId'], avit_df['AdStatus'], avit_df['Category'], avit_df['GoodsType'],  avit_df['VehicleType'], avit_df['Address'], avit_df['Condition'], avit_df['AdType'], avit_df['ContactPhone'], avit_df['DateBegin'], avit_df['DateEnd'], avit_df['AllowEmail'], avit_df['ManagerName'], avit_df['ImageNames'], avit_df['Description'], avit_df['Price'] = '', 'Free', 'Коллекционирование', 'Модели', '', 'Москва, метро Улица Скобелевская', 'Новое', 'Продаю своё', '+7 985 182-56-36', '', '', '', '', '', Description_string, ''
<ipython-input-30-d66c6d39393a>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,

In [ ]:
avit_df[:2]

SKU  \
№                  
0     ZH02192633   
1  6973130379770   

                                                              name  \
№                                                                    
0                             Space Marines Space Wolves Claw Pack   
1  Sons of Horus Ezekyle Abaddon First Captain of the XVIth Legion   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      all_img_card  \
№                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
0  https://img.joytoy.com/u_file/2403/25/photo/1-3.jpg | https://img.joytoy.com/u_file/2403/25/photo/2.jpg | https://img.joytoy.com/u_file/2403/25/photo/7.jpg | https://img.joytoy.com/u_file/2403/25/photo/4.jpg | https://img.joytoy.com/u_file/2403/25/photo/6.jpg | https://img.joytoy.com/u_file/2403/25/photo/8.jpg | https://img.joytoy.com/u_file/2403/25/photo/4-845c.jpg | https://img.joytoy.com/u_file/2403/25/photo/7-1c07.jpg | https://img.joytoy.com/u_file/2403/25/photo/2-d5ef.jpg | https://img.joytoy.com/u_file/2403/25/photo/5.jpg | https://img.joytoy.com/u_file/2403/25/photo/6-e6d4.jpg | https://img.joytoy.com/u_file/2403/25/photo/8-6603.jpg | https://img.joytoy.com/u_file/2403/25/photo/2-7a24.jpg | https://img.joytoy.com/u_file/2403/25/photo/3.jpg | https://img.joytoy.com/u_file/2403/25/photo/4-7799.jpg | https://img.joytoy.com/u_file/2403/25/photo/5-96e8.jpg | https://img.joytoy.com/u_file/2403/25/photo/7-6635.jpg | https://img.joytoy.com/u_file/2403/25/photo/8-3a6

In [ ]:
# заменяем в столбце Description заглушку {name} на значение товара из столбца name
def replace_name(row):
    return row['Description'].replace('{name}', row['name'])

avit_df['Description'] = avit_df.apply(replace_name, axis=1)

In [ ]:
avit_df

SKU  \
№                     
0        ZH02192633   
1     6973130379770   
2     6973130379787   
3        ZH18253249   
4     6973130379619   
5        ZH02968972   
6     6973130379510   
7     6973130379503   
8        ZH66738097   
9     6973130373938   
10    6973130379442   
11    6973130379411   
12       ZH74819804   
13       ZH32495625   
14         ZH364350   
15    6973130376656   
16    6973130376649   
17    6973130376632   
18    6973130376625   
19    6973130379237   
20      ZH107114121   
21    6973130379220   
22         ZH900613   
23         ZH697683   
24    6973130379145   
25    6973130379138   
26       ZH90849091   
27       ZH46536077   
28    6973130379039   
29         ZH950815   
30         ZH647188   
31    6973130378124   
32    6973130378957   
33    6973130378940   
34    6973130373297   
35         ZH462239   
36    6973130378889   
37    6973130378896   
38    6973130378902   
39    6973130378872   
40    6973130378865   
41    6973130378834   
42         ZH031027   
43   6973130378841    
44    6973130378858   
45       ZH71889501   
46    6973130378032   
47    6973130378025   
48    6973130378018   
49    6973130378155   
50    6973130378148   
51    6973130378131   
52    6973130376502   
53    6973130377325   
54    6973130377585   
55    6973130377981   
56    6973130377974   
57    6973130377967   
58    6973130377943   
59    6973130377936   
60    6973130377929   
61    6973130377912   
62    6973130377905   
63    6973130377899   
64    6973130377882   
65    6973130377844   
66    6973130377851   
67    6973130377868   
68    6973130372337   
69    6973130372344   
70    6973130372351   
71    6973130377790   
72    6973130377837   
73    6973130377820   
74    6973130377813   
75    6973130377806   
76    6973130377783   
77    6973130377745   
78    6973130377738   
79    6973130377721   
80    6973130377752   
81    6973130377714   
82    6973130377691   
83    6973130377684   
84    6973130377677   
85    6973130376434   
86    6973130377592   
87    6973130377530   
88    6973130376878   
89    6973130376885   
90    6973130376861   
91    6973130376854   
92    6973130376847   
93    6973130376816   
94    6973130376809   
95    6973130376793   
96    6973130376717   
97    6973130376700   
98    6973130376694   
99    6973130376687   
100   6973130376670   
101   6973130376663   
102   6973130376533   
103   6973130376496   
104   6973130376519   
105   6973130376526   
106   6973130376557   
107   6973130376540   
108   6973130376489   
109   6973130376465   
110   6973130376458   
111   6973130376441   
112   6973130376427   
113   6973130373587   
114   6973130376335   
115   6973130376342   
116   6973130375550   
117   6973130375543   
118   6973130375536   
119   6973130375529   
120   6973130375512   
121   6973130375505   
122   6973130375567   
123   6973130375376   
124   6973130375369   
125   6973130375352   
126   6973130375338   
127   6973130375277   
128   6973130375260   
129   6973130375253   
130   6973130375246   
131   6973130375239   
132   6973130375222   
133   6973130375215   
134   6973130375321   
135   6973130375314   
136   6973130375284   
137   6973130375307   
138   6973130375208   
139   6973130375161   
140   6973130375154   
141   6973130375147   
142   6973130375130   
143   6973130375123   
144   6973130375048   
145   6973130375031   
146   6973130375024   
147   6973130375017   
148   6973130375000   
149   6973130375086   
150   6973130375079   
151   6973130375062   
152   6973130374966   
153   6973130374959   
154   6973130374942   
155   6973130374935   
156   6973130374867   
157   6973130374850   
158   6973130374843   
159   6973130374768   
160   6973130374782   
161   6973130374775   
162   6973130372474   
163   6973130372498   
164   6973130374553   
165   6973130374546   
166   6973130374607   
167   6973130374591   
168   6973130374584   
169   6973130374577   
170   6973130374638   
171   6973130374621   
172   69731303

In [ ]:
# Выполняем переименование столбцов под требования шаблона
new_column_name = ['Id', 'Title', 'ImageUrls']
old_column_name = ['SKU', 'name', 'all_img_card'] # имя столбца, которое вы хотите изменить
avit_df.rename(columns=dict(zip(old_column_name, new_column_name)), inplace=True)

In [ ]:
# Функция для оставления части строки по количеству вхождения символа
def keep_part_by_char_count(string, char, count):
    # Ищем индексы вхождений символа
    indices = [i for i, c in enumerate(string) if c == char]
    if len(indices) < count:
        return string
    else:
        return string[:indices[count-1]+1]

# Применяем функцию к определенным строкам в столбце 'text'
char = '|'
count = 9
avit_df['ImageUrls'] = avit_df['ImageUrls'].apply(lambda x: keep_part_by_char_count(x, char, count))

In [ ]:
# Выводим столбцы в порядке шаблона
avit_df_final = avit_df[['Id', 'AvitoId', 'AdStatus', 'Category', 'GoodsType', 'VehicleType', 'Address', 'Title', 'Description', 'Condition', 'Price', 'AdType', 'DateBegin', 'DateEnd', 'AllowEmail', 'ManagerName', 'ContactPhone', 'ImageNames', 'ImageUrls']]
avit_df_final

Id AvitoId AdStatus            Category GoodsType  \
№                                                                    
0        ZH02192633             Free  Коллекционирование    Модели   
1     6973130379770             Free  Коллекционирование    Модели   
2     6973130379787             Free  Коллекционирование    Модели   
3        ZH18253249             Free  Коллекционирование    Модели   
4     6973130379619             Free  Коллекционирование    Модели   
5        ZH02968972             Free  Коллекционирование    Модели   
6     6973130379510             Free  Коллекционирование    Модели   
7     6973130379503             Free  Коллекционирование    Модели   
8        ZH66738097             Free  Коллекционирование    Модели   
9     6973130373938             Free  Коллекционирование    Модели   
10    6973130379442             Free  Коллекционирование    Модели   
11    6973130379411             Free  Коллекционирование    Модели   
12       ZH74819804             Free  Коллекционирование    Модели   
13       ZH32495625             Free  Коллекционирование    Модели   
14         ZH364350             Free  Коллекционирование    Модели   
15    6973130376656             Free  Коллекционирование    Модели   
16    6973130376649             Free  Коллекционирование    Модели   
17    6973130376632             Free  Коллекционирование    Модели   
18    6973130376625             Free  Коллекционирование    Модели   
19    6973130379237             Free  Коллекционирование    Модели   
20      ZH107114121             Free  Коллекционирование    Модели   
21    6973130379220             Free  Коллекционирование    Модели   
22         ZH900613             Free  Коллекционирование    Модели   
23         ZH697683             Free  Коллекционирование    Модели   
24    6973130379145             Free  Коллекционирование    Модели   
25    6973130379138             Free  Коллекционирование    Модели   
26       ZH90849091             Free  Коллекционирование    Модели   
27       ZH46536077             Free  Коллекционирование    Модели   
28    6973130379039             Free  Коллекционирование    Модели   
29         ZH950815             Free  Коллекционирование    Модели   
30         ZH647188             Free  Коллекционирование    Модели   
31    6973130378124             Free  Коллекционирование    Модели   
32    6973130378957             Free  Коллекционирование    Модели   
33    6973130378940             Free  Коллекционирование    Модели   
34    6973130373297             Free  Коллекционирование    Модели   
35         ZH462239             Free  Коллекционирование    Модели   
36    6973130378889             Free  Коллекционирование    Модели   
37    6973130378896             Free  Коллекционирование    Модели   
38    6973130378902             Free  Коллекционирование    Модели   
39    6973130378872             Free  Коллекционирование    Модели   
40    6973130378865             Free  Коллекционирование    Модели   
41    6973130378834             Free  Коллекционирование    Модели   
42         ZH031027             Free  Коллекционирование    Модели   
43   6973130378841              Free  Коллекционирование    Модели   
44    6973130378858             Free  Коллекционирование    Модели   
45       ZH71889501             Free  Коллекционирование    Модели   
46    6973130378032             Free  Коллекционирование    Модели   
47    6973130378025             Free  Коллекционирование    Модели   
48    6973130378018             Free  Коллекционирование    Модели   
49    6973130378155             Free  Коллекционирование    Модели   
50    6973130378148             Free  Коллекционирование    Модели   
51    6973130378131             Free  Коллекционирование    Модели   
52    6973130376502             Free  Коллекционирование    Модели   
53    6973130377325             Free  Коллекционирование    Модели   
54    6973130377585             Free  Коллекционирование    Модели   
55    6973130377981        

**СОХРАНЯЕМ ФАЙЛ ЭКСЕЛЬ**

In [ ]:
file_path = r"C:\Users\Fibo\Проекты\WH40\avito_df.xlsx"

avit_df_final.to_excel(file_path, index=False)

## --> ФОРМИРОВАНИЕ ФАЙЛОВ ДЛЯ ВК

In [ ]:
object_string = """
      <offer id="6973130379572" available="true">
        <price>3500</price>
        <count>0</count>
        <currencyId>RUB</currencyId>
        <name>Sons of Horus MKIV Sergeant with Power Fist</name>
        <description>Sons of Horus MKIV Sergeant with Power Fist</description>
        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7488.jpg</picture>
        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7489.jpg</picture>
        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7493.jpg</picture>
        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7494.jpg</picture>
        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7539.jpg</picture>
"""

In [ ]:
object_string

'\n      <offer id="6973130379572" available="true">\n        <price>3500</price>\n        <count>0</count>\n        <currencyId>RUB</currencyId>\n        <name>Sons of Horus MKIV Sergeant with Power Fist</name>\n        <description>Sons of Horus MKIV Sergeant with Power Fist</description>\n        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7488.jpg</picture>\n        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7489.jpg</picture>\n        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7493.jpg</picture>\n        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7494.jpg</picture>\n        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7539.jpg</picture>\n'

In [ ]:
# Получаем шаблон YAML файла созданного бородой для ВК

file_path = "/content/VK_19.03.xml" # шаблон предварительно был загружен в каталог колаба в разелел файлов

with open (file_path) as f:
    data = f.read(1500) #вывод количества символов
print(data)

<?xml version="1.0" encoding="utf-8"?>
<yml_catalog date="2021-04-01 12:20">
  <shop>
    <name>JoyToy - Warhammer 40000, Dark Source, Infinity</name>
    <company>JoyToy - Warhammer 40000, Dark Source, Infinity</company>
    <url>https://vk.com/joytoy40k/</url>
    <currencies>
      <currency id="RUB" rate="1"/>
    </currencies>
    <categories>
      <category id="11">Warhammer 400001</category>
      <category id="2">Dark Source</category>
      <category id="3">В наличии</category>
      <category id="4">Предзаказ</category>
    </categories>
    <offers>
      <offer id="6973130379572" available="true">
        <price>3500</price>
        <count>0</count>
        <currencyId>RUB</currencyId>
        <name>Sons of Horus MKIV Sergeant with Power Fist</name>
        <description>Sons of Horus MKIV Sergeant with Power Fist</description>
        <picture>https://img.joytoy.com/u_file/2402/29/photo/262A7488.jpg</picture>
        <picture>https://img.joytoy.com/u_file/2402/29/photo/262